In [196]:
import json
import codecs
import os
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from collections import Counter
from sklearn.cluster import KMeans
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.metrics import silhouette_score
pd.options.display.max_rows = 200
#pd.reset_option('display')

<h2>Gathering the Data</h2>
<p>In this initial section, we will gather all of the cuneiform sign transliterations from the JSON files in our dataset. Then we will consolidate them into a data frame and add other columns to help our computations.</p>

<p>First, we will load a map from sign value to sign name to use on the signs in our texts. The OGSL is... (website...)</p>

In [2]:
file_ogsl = codecs.open('ogsl-sl.json','r','utf-8')
ogsl = json.load(file_ogsl)
sign_index = ogsl['index']

<h3>Collect the Text Signs</h3>
<p>The following code parses the JSON files of the ORACC texts and collects each sign transliteration. Since different signs have different types of reading, they are rendered differently in the JSON file and we must take care to recognize each sign reading type in the JSON file</p>
The types of signs and their representation in the JSON Files:
<ol>
    <li>Syllable - The reading of a sign as a syllable is rendered with a 'v' key</li>
    <li>Logogram - The reading of a sign as a logogram, i.e. one represents a word in itself or as part of a complex of signs that represents a single word is written in capital letters and with a 's' key</li>
    <li>Numerical - A sign representing a number (or personal name determinative) has an extra key called 'sexified'. This gives information on the number sign's wedge structure.</li>
</ol>

In addition, a modified sign can be any of the three types above, but written with a nonstandard paleography (e.g. a diagonal wedge is incised in the clay instead of a horizontal). These are the signs we want to examine. They have extra data given under the 'mods' key.

In [3]:
def process_signs(sign_data):
    sign_info = {}
    if 'v' in sign_data: #This is the label for a standard syllable
        sign_info['b'] = sign_data['v']
    if 's' in sign_data: #This is the label for elements of a logogram
        sign_info['b'] = sign_data['s']
    if 'n' in sign_data:
        sign_info['b'] = sign_data.get('sexified',sign_data.get('form','noform?'))
    if 'mods' in sign_data:
        for m in sign_data['mods']:
            for d in m:
                sign_info[d] = m[d]
    if 'break' in sign_data:
        sign_info['break'] = sign_data['break']
    sign_info['sign_loc_id'] = sign_data.get('id','no-id')
    return sign_info    

In [116]:
def parse_corpus(corpus_name):
    types = set()
    all_signs = []
    all_words = []
    for fname in os.listdir(corpus_name + '/corpusjson'):
        f = codecs.open(corpus_name + '/corpusjson/'+fname,'r','utf-8')
        try:
            j = json.load(f)
        except ValueError:
            print('Could not load: ' + fname)
            continue
        text_id = j['textid']
        for a in j['cdl'][0]['cdl']:
            if a.get('type','') == 'discourse':
                for b in a['cdl']:
                    if b.get('type','') == 'sentence':
                        line_label = ''
                        word_count = 0
                        for c in b['cdl']:
                            if c.get('node','') == 'd': #This is the label for the line e.g. "o ii 3"
                                line_label = c.get('label','nolabel')
                            if c.get('node','') == 'l': #This is the label for a regular word in a line
                                if c.get('tail-sig','') != '': #An extra word??
                                    continue
                                word_count += 1
                                form = c['f']['form']
                                frag = c['frag']
                                ref  = c['ref']
                                cf   = c['f'].get('cf','no-cf')
                                gw   = c['f'].get('gw','no-gw')
                                pos  = c['f'].get('pos','no-pos')
                                sense = c['f'].get('sense','no-sense')
                                norm = c['f'].get('norm','no-norm')
                                epos = c['f'].get('epos','no-epos')
                                word_sign_tot = len(c['f']['gdl'])
                                word_info = {'file':fname,'line_label':line_label,'form': form,'frag': frag, 'text_id': text_id,
                                             'ref': ref,'cf': cf,'gw': gw,'pos': pos,'epos':epos,
                                             'sense':sense,'word_sign_tot':word_sign_tot,'norm':norm,'word_num': word_count}
                                all_words.append(word_info)
                                for sign_data in c['f']['gdl']:
                                    if sign_data.get('det','') == 'semantic':
                                        for sd in sign_data['seq']:
                                            if sd.get('gg','') == 'logo':
                                                for g in sd['group']:
                                                    sign_info = process_signs(g)
                                                    sign_info.update(word_info)
                                                    all_signs.append(sign_info)
                                            else:
                                                sign_info = process_signs(sd)
                                                sign_info.update(word_info)
                                                all_signs.append(sign_info)
                                    elif sign_data.get('gg','') == 'logo':
                                        for g in sign_data['group']:
                                            if g.get('det','') == 'semantic':
                                                for sd in g['seq']:
                                                    if sd.get('gg','') == 'logo':
                                                        for gg in sd['group']:
                                                            sign_info = process_signs(gg)
                                                            sign_info.update(word_info)
                                                            all_signs.append(sign_info)                                       
                                                    else:
                                                        sign_info = process_signs(sd)
                                                        sign_info.update(word_info)
                                                        all_signs.append(sign_info)                                       
                                            else:
                                                sign_info = process_signs(g)
                                                sign_info.update(word_info)
                                                all_signs.append(sign_info)                                        
                                    else:
                                        sign_info = process_signs(sign_data)
                                        sign_info.update(word_info)
                                        all_signs.append(sign_info)
                            '''
                            if c.get('node','') == 'c': #This is the label for a phrase. This seems to no longer be used 
                                for d in c['cdl']:
                                    if d.get('node','') == 'l':
                                        form = d['f']['form']
                                        for sign_data in d['f']['gdl']:
                                            if sign_data.get('det','') == 'semantic':
                                                for sd in sign_data['seq']:
                                                    sign_info = process_signs(sd)
                                                    sign_info.update({'file':fname,'line_label':line_label,'form': form})
                                                    all_signs.append(sign_info)
                                            else:
                                                sign_info = process_signs(sign_data)
                                                sign_info.update({'file':fname,'line_label':line_label,'form': form})
                                                all_signs.append(sign_info)
                            '''
                            #types.add(c.get('type','no type'))

    print('done')
    return all_signs,all_words

In [109]:
sargon_signs,sargon_words = parse_corpus('sargonletters')

Could not load: P314095.json
done


In [110]:
df_sargon = pd.DataFrame(sargon_signs)
df_sargon = df_sargon.fillna('')
df_sargon

a            b    break                cf     epos  f          file  \
0                    a  damaged             awātu        N     P224485.json   
1                  bat                      awātu        N     P224485.json   
2                LUGAL                      šarru        N     P224485.json   
3                    a                        ana      PRP     P224485.json   
4                   na                        ana      PRP  t  P224485.json   
5               1(diš)           Aššur-šarru-uṣur       PN     P224485.json   
6                   aš           Aššur-šarru-uṣur       PN     P224485.json   
7                  šur           Aššur-šarru-uṣur       PN     P224485.json   
8                  MAN           Aššur-šarru-uṣur       PN     P224485.json   
9                  PAB  damaged  Aššur-šarru-uṣur       PN     P224485.json   
10                 šul  damaged             šulmu        N     P224485.json   
11                  mu                      šulmu        N     P224485.json   
12                  ia                      yâšim       IP     P224485.json   
13                   a  damaged             yâšim       IP     P224485.json   
14                  ši                      yâšim       IP     P224485.json   
15                 šul  damaged             šulmu        N     P224485.json   
16                  mu                      šulmu        N     P224485.json   
17                   a                        ana      PRP     P224485.json   
18                  na                        ana      PRP  t  P224485.json   
19                 KUR                  Mat-Aššur       GN     P224485.json   
20                  aš                  Mat-Aššur       GN     P224485.json   
21                 šur                  Mat-Aššur       GN     P224485.json   
22                  KI                  Mat-Aššur       GN     P224485.json   
23                 ŠA₃  damaged             libbu        N     P224485.json   
24                  ka  missing             libbu        N     P224485.json   
25                  lu  damaged                lū      MOD     P224485.json   
26                DUG₃                       ṭābu       AJ     P224485.json   
27                  GA                       ṭābu       AJ     P224485.json   
28                  ka                       ṭābu       AJ     P224485.json   
29                  ša  damaged                ša      REL     P224485.json   
30                 taš                     šapāru        V     P224485.json   
31                 pur                     šapāru        V     P224485.json   
32                  an                     šapāru        V     P224485.json   
33                  ni                     šapāru        V     P224485.json   
34                  ma                         mā      PRP     P224485.json   
35                   a                         mā      PRP     P224485.json   
36      v          LU₂                       māru        N     P224485.json   
37                   A                       māru        N     P224485.json   
38                 šip                       māru        N     P224485.json   
39                  ri  damaged              māru        N     P224485.json   
40                  ša  missing                ša      DET     P224485.json   
41              1(diš)                       Mita       PN     P224485.json   
42                  me                       Mita       PN     P224485.json   
43                  ta                       Mita       PN     P224485.json   
44                   a                       Mita       PN     P224485.json   
45                 KUR                    Muskaya       EN     P224485.json   
46                 mus                    Muskaya       EN     P224485.json   
47                  ka                    Muskaya       EN     P224485.json   
48                   a                    Muskaya       EN     P224485.json   
49                   a                    Muskaya       EN

Now, we form our Data Frame where each row contains information on every sign in the corpus. Further limitations on which signs are significant to our purposes will be made later, but for now we will eliminate all of the signs which are labelled as "missing," (i.e. reconstructed) because any information based on their paleography or orthography cannot be ascertained.

In [99]:
df = pd.DataFrame(all_signs)
df = df.fillna('')
df

a            b    break                cf     epos  f          file  \
0                    a  damaged             awātu        N     P224485.json   
1                  bat                      awātu        N     P224485.json   
2                LUGAL                      šarru        N     P224485.json   
3                    a                        ana      PRP     P224485.json   
4                   na                        ana      PRP  t  P224485.json   
5               1(diš)           Aššur-šarru-uṣur       PN     P224485.json   
6                   aš           Aššur-šarru-uṣur       PN     P224485.json   
7                  šur           Aššur-šarru-uṣur       PN     P224485.json   
8                  MAN           Aššur-šarru-uṣur       PN     P224485.json   
9                  PAB  damaged  Aššur-šarru-uṣur       PN     P224485.json   
10                 šul  damaged             šulmu        N     P224485.json   
11                  mu                      šulmu        N     P224485.json   
12                  ia                      yâšim       IP     P224485.json   
13                   a  damaged             yâšim       IP     P224485.json   
14                  ši                      yâšim       IP     P224485.json   
15                 šul  damaged             šulmu        N     P224485.json   
16                  mu                      šulmu        N     P224485.json   
17                   a                        ana      PRP     P224485.json   
18                  na                        ana      PRP  t  P224485.json   
19                 KUR                  Mat-Aššur       GN     P224485.json   
20                  aš                  Mat-Aššur       GN     P224485.json   
21                 šur                  Mat-Aššur       GN     P224485.json   
22                  KI                  Mat-Aššur       GN     P224485.json   
23                 ŠA₃  damaged             libbu        N     P224485.json   
24                  ka  missing             libbu        N     P224485.json   
25                  lu  damaged                lū      MOD     P224485.json   
26                DUG₃                       ṭābu       AJ     P224485.json   
27                  GA                       ṭābu       AJ     P224485.json   
28                  ka                       ṭābu       AJ     P224485.json   
29                  ša  damaged                ša      REL     P224485.json   
30                 taš                     šapāru        V     P224485.json   
31                 pur                     šapāru        V     P224485.json   
32                  an                     šapāru        V     P224485.json   
33                  ni                     šapāru        V     P224485.json   
34                  ma                         mā      PRP     P224485.json   
35                   a                         mā      PRP     P224485.json   
36      v          LU₂                       māru        N     P224485.json   
37                   A                       māru        N     P224485.json   
38                 šip                       māru        N     P224485.json   
39                  ri  damaged              māru        N     P224485.json   
40                  ša  missing                ša      DET     P224485.json   
41              1(diš)                       Mita       PN     P224485.json   
42                  me                       Mita       PN     P224485.json   
43                  ta                       Mita       PN     P224485.json   
44                   a                       Mita       PN     P224485.json   
45                 KUR                    Muskaya       EN     P224485.json   
46                 mus                    Muskaya       EN     P224485.json   
47                  ka                    Muskaya       EN     P224485.json   
48                   a                    Muskaya       EN     P224485.json   
49                   a                    Muskaya       EN

<h3>Setting Up the Data for Clustering</h3>
<p>The general goal is to assign a vector to each text that reflects the usage of variant orthography and paleography.</p>
<ol>
    <li>Paleography - Any one set of wedges that we classify as a sign can be impressed on the clay in different ways. For example, a wedge can be missing or one can be added. Also, the tilt of a wedge can variable. These are the features we want to examine in order to see if one text prefers one sign writing or another.</li>
    <li>Orthography - Due to the homophony of the cuneiform writing system, one syllable can be written with many signs. For example, 'li' can be written with the LI-sign but also with the NI-sign, in which case it would be transliterated as li<sub>2</sub></li>
    <li>Orthography (Words) - In addition to syllables being written by variant sign forms, a word (with appropriate inflection) can be written in different ways similar to how "color" is written "colour" in British English. These two variant orthographies indicate the same word but their variation might indicate something about the author.</li>
</ol>

<p>This section therefore contains three subsections. One groups the diagnostic signs with or without modifications per text to. The next discovers the homophonous signs used throughout the corpus and groups different usages per text. The third groups the word forms in the corpus.</p>

First of all, let's create more columns in the data frame to aid us
<ol>
<li>sign_form - Using the OGSL mapping we created earlier, we can assign each reading of a sign to its sign form. This will help us combine different readings under the same sign form to help us mark variations in paleography</li>
<li>mods_str - Since the data contains three columns currently with information on variable paleography, it would help us to consolidate them into one column</li>
<li>combined - This column combines sign_form and mods_str into one string similar to how the <i>b</i> column is a combination of str_part and num_part</li>
<li>str_part and num_part - In order to determine which signs share a syllabic value, it will be useful to separate the transliterated readings into their string components and numerical components. Once we do this, we can group rows with the same str_part and count up the different usages of homophonous signs</li>
</ol>

In [100]:
file_names = df['file'].unique()
df['sign_form'] = df['b'].apply(lambda x: sign_index.get(x.lower(),'?'))
df['mods_str'] = df['a'] + '.' + df['f']  + '.' + df['m']

import re
def get_num_part(s):
    try:
        n = re.findall(r'[₀₁₂₃₄₅₆₇₈₉]+',s)[0]
        n = n.replace('₀','0').replace('₁','1').replace('₂','2').replace('₃','3').replace('₄','4')
        n = n.replace('₅','5').replace('₆','6').replace('₇','7').replace('₈','8').replace('₉','9')
    except:
        n = 1
    return n
def get_str_part(s):
    try:
        n = re.findall(r'[a-zA-ZšŠṣṢṭṬʾ \(\)0-9]+',s)[0]
    except:
        n = s
    return n
        
df['str_part'] = df['b'].apply(lambda x: get_str_part(x))
df['num_part'] = df['b'].apply(lambda x: get_num_part(x))
df['combined'] = df['sign_form'] + ':' + df['mods_str']
df

a            b    break                cf     epos  f          file  \
0                    a  damaged             awātu        N     P224485.json   
1                  bat                      awātu        N     P224485.json   
2                LUGAL                      šarru        N     P224485.json   
3                    a                        ana      PRP     P224485.json   
4                   na                        ana      PRP  t  P224485.json   
5               1(diš)           Aššur-šarru-uṣur       PN     P224485.json   
6                   aš           Aššur-šarru-uṣur       PN     P224485.json   
7                  šur           Aššur-šarru-uṣur       PN     P224485.json   
8                  MAN           Aššur-šarru-uṣur       PN     P224485.json   
9                  PAB  damaged  Aššur-šarru-uṣur       PN     P224485.json   
10                 šul  damaged             šulmu        N     P224485.json   
11                  mu                      šulmu        N     P224485.json   
12                  ia                      yâšim       IP     P224485.json   
13                   a  damaged             yâšim       IP     P224485.json   
14                  ši                      yâšim       IP     P224485.json   
15                 šul  damaged             šulmu        N     P224485.json   
16                  mu                      šulmu        N     P224485.json   
17                   a                        ana      PRP     P224485.json   
18                  na                        ana      PRP  t  P224485.json   
19                 KUR                  Mat-Aššur       GN     P224485.json   
20                  aš                  Mat-Aššur       GN     P224485.json   
21                 šur                  Mat-Aššur       GN     P224485.json   
22                  KI                  Mat-Aššur       GN     P224485.json   
23                 ŠA₃  damaged             libbu        N     P224485.json   
24                  ka  missing             libbu        N     P224485.json   
25                  lu  damaged                lū      MOD     P224485.json   
26                DUG₃                       ṭābu       AJ     P224485.json   
27                  GA                       ṭābu       AJ     P224485.json   
28                  ka                       ṭābu       AJ     P224485.json   
29                  ša  damaged                ša      REL     P224485.json   
30                 taš                     šapāru        V     P224485.json   
31                 pur                     šapāru        V     P224485.json   
32                  an                     šapāru        V     P224485.json   
33                  ni                     šapāru        V     P224485.json   
34                  ma                         mā      PRP     P224485.json   
35                   a                         mā      PRP     P224485.json   
36      v          LU₂                       māru        N     P224485.json   
37                   A                       māru        N     P224485.json   
38                 šip                       māru        N     P224485.json   
39                  ri  damaged              māru        N     P224485.json   
40                  ša  missing                ša      DET     P224485.json   
41              1(diš)                       Mita       PN     P224485.json   
42                  me                       Mita       PN     P224485.json   
43                  ta                       Mita       PN     P224485.json   
44                   a                       Mita       PN     P224485.json   
45                 KUR                    Muskaya       EN     P224485.json   
46                 mus                    Muskaya       EN     P224485.json   
47                  ka                    Muskaya       EN     P224485.json   
48                   a                    Muskaya       EN     P224485.json   
49                   a                    Muskaya       EN

<h3>Paleography Setup</h3>
<p>The Data Frame we have contains the entire collection of signs in the corpus. However, not every sign has variants in paleography (at least according to Parpola's data input). We only want to look at the signs which have these variants, which we will term diagnostic. In the data, they are the signs that include any type of modification</p>

In [7]:
df2 = df[~(df['mods_str'] == '..')]
list_mod_signs = sorted(list(df2['sign_form'].unique()))

df_paleo = df[df['sign_form'].isin(list_mod_signs)]

#remove damaged signs too
df_paleo = df_paleo[df_paleo['break'] != 'damaged']
df_paleo

a      b    break                cf epos  f          file  \
1            bat                      awātu    N     P224485.json   
2          LUGAL                      šarru    N     P224485.json   
3              a                        ana  PRP     P224485.json   
4             na                        ana  PRP  t  P224485.json   
7            šur           Aššur-šarru-uṣur   PN     P224485.json   
11            mu                      šulmu    N     P224485.json   
12            ia                      yâšim   IP     P224485.json   
14            ši                      yâšim   IP     P224485.json   
16            mu                      šulmu    N     P224485.json   
17             a                        ana  PRP     P224485.json   
18            na                        ana  PRP  t  P224485.json   
19           KUR                  Mat-Aššur   GN     P224485.json   
21           šur                  Mat-Aššur   GN     P224485.json   
22            KI                  Mat-Aššur   GN     P224485.json   
24            ka  missing             libbu    N     P224485.json   
26          DUG₃                       ṭābu   AJ     P224485.json   
27            GA                       ṭābu   AJ     P224485.json   
28            ka                       ṭābu   AJ     P224485.json   
30           taš                     šapāru    V     P224485.json   
31           pur                     šapāru    V     P224485.json   
33            ni                     šapāru    V     P224485.json   
34            ma                         mā  PRP     P224485.json   
35             a                         mā  PRP     P224485.json   
36      v    LU₂                       māru    N     P224485.json   
37             A                       māru    N     P224485.json   
38           šip                       māru    N     P224485.json   
40            ša  missing                ša  DET     P224485.json   
42            me                       Mita   PN     P224485.json   
43            ta                       Mita   PN     P224485.json   
44             a                       Mita   PN     P224485.json   
...    ..    ...      ...               ...  ... ..           ...   
155021      ANŠE                       sisû    N     X900015.json   
155022       KUR                       sisû    N     X900015.json   
155023        RA                       sisû    N     X900015.json   
155024       MEŠ                       sisû    N     X900015.json   
155025        ni                       leqû    V     X900015.json   
155026       laq                       leqû    V     X900015.json   
155027        qi                       leqû    V     X900015.json   
155028        nu                     wabālu    V     X900015.json   
155029       bal                     wabālu    V     X900015.json   
155030       kal                      kallû    N     X900015.json   
155031        li                      kallû    N     X900015.json   
155032        u₂                      kallû    N     X900015.json   
155033        ša                         ša  DET     X900015.json   
155036       šur           Aššur-daʾʾinanni   PN     X900015.json   
155037     KALAG           Aššur-daʾʾinanni   PN     X900015.json   
155039        ni           Aššur-daʾʾinanni   PN     X900015.json   
155040        ša                    šaṣbutu    N     X900015.json   
155042        bu                    šaṣbutu    N     X900015.json   
155043       tu₂                    šaṣbutu    N     X900015.json   
155044        ša                         ša  DET     X900015.json   
155045       URU                 Arzuhinaya   EN     X900015.json   
155046       ar₂                 Arzuhinaya   EN     X900015.json   
155047        zu                 Arzuhinaya   EN     X900015.json   
155048        hi                 Arzuhinaya   EN     X900015.json   
155049        na                 Arzuhinaya   EN     X900015.json   
155050         a                 Arzuhinaya   EN     X900015.json   
155051

Create the text matrix with raw counts

In [8]:
df_paleo_str = pd.DataFrame(df_paleo.groupby(['text_id']).apply(lambda x: ' '.join(x['combined'])))
df_paleo_str.columns = ['paleo_str']
df_paleo_str

cv = CountVectorizer(token_pattern='[^ ]+',lowercase=False)
ft = cv.fit_transform(list(df_paleo_str['paleo_str']))
tm_paleo = pd.DataFrame(ft.toarray(),columns=cv.get_feature_names(),index=df_paleo_str.index)
tm_paleo

A:..  A:.d.  AB@g:..  AB@g:.m.  AB@g:.p.  AB₂:..  AB₂:.d.  AK:..  \
text_id                                                                     
P224485   104      0        1         0         0       1        0      1   
P237089     5      0        0         0         0       0        0      0   
P238649     5      0        0         0         0       0        0      0   
P313416     2      0        0         0         0       0        0      0   
P313417    39      0        0         0         0       0        0      0   
P313419    16      0        0         0         0       0        0      0   
P313420    13      0        0         0         0       0        0      0   
P313421     6      0        0         0         0       0        0      0   
P313422    10      0        0         0         0       0        0      0   
P313425    47      0        0         0         0       0        0      0   
P313427    11      0        0         0         0       0        0      1   
P313434    11      0        0         0         0       0        0      0   
P313435     8      0        0         0         0       0        0      0   
P313437     5      0        0         0         0       0        0      0   
P313439    19      0        0         0         0       2        0      0   
P313442    11      0        0         0         0       0        0      0   
P313444     9      0        0         0         0       0        0      0   
P313445     3      0        0         0         0       0        0      0   
P313447    20      0        0         0         0       0        0      1   
P313448    10      0        0         0         0       0        0      0   
P313450    41      0        0         0         0       0        0      0   
P313451    10      0        0         0         0       0        0      0   
P313452    67      0        0         0         0       0        0      1   
P313453    14      0        0         0         0       0        0      0   
P313454     8      0        0         0         0       0        0      0   
P313455     6      0        0         0         0       0        0      0   
P313457    11      0        0         0         0       1        0      0   
P313458    12      0        0         0         0       3        0      0   
P313462    11      0        0         0         0       0        0      0   
P313469     6      0        0         0         0       0        0      0   
...       ...    ...      ...       ...       ...     ...      ...    ...   
P336178     3      0        0         0         0       0        0      0   
P336595     4      0        0         0         0       0        0      0   
P336596     2      0        0         0         0       0        0      0   
P336597     2      0        0         0         0       0        0      0   
P336635     6      0        0         0         0       0        0      0   
P336636     2      0        0         0         0       0        0      0   
P336768     4      0        0         0         0       0        0      0   
P336769     2      0        0         0         0       0        0      0   
P336770     2      0        0         0         0       0        0      0   
P336771     2      0        0         0         0       0        0      0   
P336772     2      0        0         0         0       0        0      0   
P336773     0      0        0         0         0       0        0      0   
P336774     6      0        0         0         0       0        0      0   
P336775     1      0        0         0         0       0        0      0   
P336776     1      0        0         0         0       0        0      0   
P337150    35      0        0         0         0       0        0      1   
P337151    21      0        0         0         0       0        0      0   
P393855     4      0        0         0         0       0        0      0   
P393866    11      0        0         0         0       0        0      0   
X9000

<h3>Orthography Syllable Setup</h3>
<p>We now limit the original data frame in different way based on orthography. First we need to figure out which syllabic readings have multiple signs that can render them. We then eliminate capital letter entries because indices on logograms indicate different words and are not relevant here. Last, we limit the data frame to only these signs.

In [9]:
df2 = pd.DataFrame(df.groupby(['str_part'])['num_part'].agg('nunique'))
list_ortho_syls = list(df2[df2[('num_part')] > 1].index)

list_ortho_syls = [h for h in list_ortho_syls if len(re.findall(r'[A-Z]',h)) == 0]
list_ortho_syls

df_ortho_signs = df[df['str_part'].isin(list_ortho_syls)]
df_ortho_signs

a     b    break                cf     epos f           file  \
0            a  damaged             awātu        N     P224485.json   
3            a                        ana      PRP     P224485.json   
6           aš           Aššur-šarru-uṣur       PN     P224485.json   
12          ia                      yâšim       IP     P224485.json   
13           a  damaged             yâšim       IP     P224485.json   
17           a                        ana      PRP     P224485.json   
20          aš                  Mat-Aššur       GN     P224485.json   
24          ka  missing             libbu        N     P224485.json   
28          ka                       ṭābu       AJ     P224485.json   
29          ša  damaged                ša      REL     P224485.json   
35           a                         mā      PRP     P224485.json   
40          ša  missing                ša      DET     P224485.json   
42          me                       Mita       PN     P224485.json   
44           a                       Mita       PN     P224485.json   
47          ka                    Muskaya       EN     P224485.json   
48           a                    Muskaya       EN     P224485.json   
49           a                    Muskaya       EN     P224485.json   
53          ia                      muhhu        N     P224485.json   
56          ka                      alāku        V     P224485.json   
58           a                         mā      PRP     P224485.json   
64           u                     Quwaya       EN     P224485.json   
65           a                     Quwaya       EN     P224485.json   
66           a  damaged            Quwaya       EN     P224485.json   
67          ša  damaged                ša      REL     P224485.json   
69          u₂  damaged              Urik       PN     P224485.json   
72           a                        ana      PRP     P224485.json   
78           a                        ana      PRP     P224485.json   
82          u₂                     wabālu        V     P224485.json   
86           u                     wabālu        V     P224485.json   
89           a                         mā      PRP     P224485.json   
...    ..  ...      ...               ...      ... ..           ...   
154955      ku                      anāku       IP     X900015.json   
154956      ša                         ša      REL     X900015.json   
154958      be                       bēlu        N     X900015.json   
154959     li₂                       bēlu        N     X900015.json   
154965       a                         mā      PRP     X900015.json   
154972       i                       išti      PRP     X900015.json   
154974      ka                       išti      PRP     X900015.json   
154976      li                      alāku        V     X900015.json   
154977      ku  damaged             alāku        V     X900015.json   
154981      tu                      hubtu        N     X900015.json   
154982       a                   adakanni       AV     X900015.json   
154983      da  damaged          adakanni       AV     X900015.json   
154984      ka  damaged          adakanni       AV     X900015.json   
154986       i  damaged             no-cf  no-epos     X900015.json   
155010     šu₂                       pānu        N     X900015.json   
155013       a  damaged                mā      PRP     X900015.json   
155017       a                         lā      MOD     X900015.json   
155019      ku                      alāku        V     X900015.json   
155027      qi                       leqû        V     X900015.json   
155030     kal                      kallû        N     X900015.json   
155031      li                      kallû        N     X900015.json   
155032      u₂                      kallû        N     X900015.json   
155033      ša                         ša      DET     X900015.json   
155035      aš           Aššur-daʾʾinanni       PN     X900015.json   
155040      ša                 

Create the text matrix with raw counts

In [10]:
df_ortho_str = pd.DataFrame(df_ortho_signs.groupby(['text_id']).apply(lambda x: ' '.join(x['b'])))
df_ortho_str.columns = ['ortho_str']
df_ortho_str

cv = CountVectorizer(token_pattern='[^ ]+',lowercase=False)
ft = cv.fit_transform(list(df_ortho_str['ortho_str']))
tm_ortho_sign = pd.DataFrame(ft.toarray(),columns=cv.get_feature_names(),index=df_ortho_str.index)
tm_ortho_sign

a  ana  ana₃  ar  ar₂  aš  aš₂  a₂  be  be₂ ...   ša₂  šu  šum  \
text_id                                                ...                  
P224485  103    2     0   6    0   5    8   0   7    2 ...     5   4    1   
P237089    5    0     0   0    0   0    0   0   2    0 ...     0   1    0   
P238649    5    0     0   0    0   0    1   0   0    0 ...     0   0    0   
P313416    3    0     0   0    0   0    0   0   3    0 ...     0   0    0   
P313417   36    0     0   0    0   1    2   0   0    0 ...     0   8    0   
P313419   16    0     0   0    0   0    0   0   0    0 ...     1   0    0   
P313420   14    1     0   1    0   1    0   0   6    0 ...     0   0    0   
P313421    7    0     0   0    0   1    0   0   1    0 ...     0   0    0   
P313422   11    1     0   2    0   1    1   0   1    1 ...     0   0    0   
P313425   51    0     0   5    0   0    1   0   5    0 ...     3   3    1   
P313427   12    0     0   0    0   0    0   0   9    0 ...     1   0    0   
P313434   10    0     0   0    0   0    0   0   2    0 ...     0   1    0   
P313435    9    0     0   0    0   1    0   0   0    0 ...     0   0    0   
P313437    5    0     0   0    0   3    0   0   0    0 ...     0   0    0   
P313439   16    0     0   0    2   2    1   0   0    0 ...     0   1    1   
P313442   15    0     0   0    2   0    0   0   0    0 ...     3   3    0   
P313444    9    0     0   0    0   0    0   0   0    0 ...     0   0    0   
P313445    3    0     0   0    0   0    1   0   2    0 ...     0   1    0   
P313447   20    0     0   0    0   2    2   0   3    0 ...     2   0    0   
P313448   10    0     0   0    0   1    2   0   3    0 ...     0   1    0   
P313450   41    1     0   0    1   2    1   0   0    0 ...     0   0    0   
P313451   10    0     0   1    0   2    0   0   0    0 ...     0   3    0   
P313452   57    1     0   0    0   0    3   0   2    0 ...     3   0    0   
P313453   16    0     0   1    0   0    1   0   0    0 ...     2   1    0   
P313454    8    0     0   0    0   0    0   0   0    0 ...     0   0    1   
P313455    6    0     0   0    0   0    1   0   1    0 ...     1   0    0   
P313457   11    0     0   0    0   1    0   0   3    1 ...     0   2    0   
P313458   12    1     0   0    0   2    2   0   2    0 ...     6   1    0   
P313462   12    0     0   0    0   3    4   0   8    0 ...     0   1    0   
P313469    7    0     0   0    0   0    0   0   0    0 ...     1   2    0   
...      ...  ...   ...  ..  ...  ..  ...  ..  ..  ... ...   ...  ..  ...   
P336178    3    0     0   0    0   0    0   0   0    0 ...     0   0    0   
P336595    4    0     0   0    1   0    0   0   0    0 ...     0   0    0   
P336596    2    0     0   0    0   1    0   0   2    0 ...     0   0    0   
P336597    4    0     0   0    0   2    0   0   2    1 ...     0   0    0   
P336635    5    0     0   0    0   0    0   0   0    0 ...     0   0    0   
P336636    2    0     0   0    0   0    0   0   1    0 ...     0   0    0   
P336768    4    0     0   0    0   0    0   0   2    0 ...     0   0    0   
P336769    1    0     0   0    0   0    0   0   0    0 ...     0   0    0   
P336770    2    0     0   0    0   0    0   0   1    0 ...     0   0    0   
P336771    2    0     0   0    0   0    0   0   1    0 ...     0   0    0   
P336772    2    0     0   0    0   0    1   0   1    0 ...     2   0    0   
P336773    0    0     0   0    0   0    0   0   0    0 ...     0   0    0   
P336774    6    0     0   0    0   0    0   0   2    0 ...     0   0    0   
P336775    1    0     0   0    0   0    0   0   0    0 ...     0   0    0   
P336776    1    0     0   0    0   0    0   0   0    0 ...     1   0    0   
P337150   35    0     0   0    0   3    0   0   5    0 ...     2   4    0   
P337151   18    0     0   0    0   1    0   0   0    0 ...     1   0    0   
P393855    4    0     0   0    1   1    1   0   3    0 ...     1   0    0   
P393866   11    0     0   1    0   0    1   0   6    2 ...     1   0    0   
X900004

<h3>Orthography Word Setup</h3>
<p>The setup for this section is slightly different. Instead of counting up every sign or reading, we count up every word, its normalization and its form. To help us out we will create two new columns <i>lemma_norm</i> and <i>lemma_norm_form</i>. The first combines the lemma and the normalized form. The latter attaches the transliteration to the former. We only want to include lemma/norm combinations that have multiple forms associated with them.

In [397]:
df_words = pd.DataFrame(all_words)
df_words = df_words[(df_words['cf'] != 'no-cf')]

df_words['lemma'] = df_words['cf'] + '[' + df_words['gw'] + ']' + df_words['pos']
df_words['lemma_norm'] = df_words['lemma'] + ':' + df_words['norm']
df_words['lemma_norm_form'] = df_words['lemma_norm'] + ':' + df_words['form']

df_norm_uniq = pd.DataFrame(df_words.groupby('lemma_norm')['form'].nunique())
list_ortho_words = list(df_norm_uniq[df_norm_uniq[('form')] > 1].index)

df_form_50 = pd.DataFrame(df_words.groupby('lemma_norm_form')['form'].agg('count'))
list_form_50 = list(df_form_50[df_form_50[('form')] > 50].index)

df_ortho_words = df_words[(df_words['lemma_norm'].isin(list_ortho_words)) & df_words['lemma_norm_form'].isin(list_form_50)]
df_ortho_words

cf epos          file              form                 frag  \
1        šarru    N  P224485.json             LUGAL                LUGAL   
2          ana  PRP  P224485.json              a-na               a-na\t   
4        šulmu    N  P224485.json            šul-mu              šul⸣-mu   
6        šulmu    N  P224485.json            šul-mu             ⸢šul⸣-mu   
7          ana  PRP  P224485.json              a-na               a-na\t   
10          lū  MOD  P224485.json                lu                 ⸢lu⸣   
12          ša  REL  P224485.json                ša                 ⸢ša⸣   
14          mā  PRP  P224485.json              ma-a                 ma-a   
16          ša  DET  P224485.json                ša                 [ša]   
19         ina  PRP  P224485.json               ina                  ina   
20       muhhu    N  P224485.json         UGU-hi-ia            UGU-hi-ia   
21       alāku    V  P224485.json         it-tal-ka          it-⸢tal⸣-ka   
22          mā  PRP  P224485.json              ma-a                 ma-a   
24        ṣābu    N  P224485.json          ERIM-MEŠ           ERIM-MEŠ\m   
26          ša  REL  P224485.json                ša                  ša⸣   
28         ana  PRP  P224485.json              a-na               a-na\t   
30         ana  PRP  P224485.json              a-na               a-na\t   
33          mā  PRP  P224485.json              ma-a                 ma-a   
34         ina  PRP  P224485.json               ina                  ina   
35       muhhu    N  P224485.json         UGU-hi-ia            UGU-hi-ia   
38     adanniš   AV  P224485.json         a-dan-niš            a-dan-niš   
39      annûri   AV  P224485.json         an-nu-rig          an-nu-rig\t   
46          lā  MOD  P224485.json                la                  la⸣   
47         ina  PRP  P224485.json               ina                  ina   
48       libbu    N  P224485.json               ŠA₃                  ŠA₃   
50          lā  MOD  P224485.json                la                  [la   
51         ina  PRP  P224485.json               ina                  ina   
52       libbu    N  P224485.json               ŠA₃                 ŠA₃]   
57         ana  PRP  P224485.json              a-na                 a-na   
60          ša  REL  P224485.json                ša                 ša\d   
62          mā  PRP  P224485.json              ma-a                 ma-a   
64       šarru    N  P224485.json             LUGAL                LUGAL   
65        bēlu    N  P224485.json         be-li₂-ia          be-li₂\d-ia   
67         ina  PRP  P224485.json               ina                  ina   
68       muhhu    N  P224485.json               UGU                  UGU   
70          lā  MOD  P224485.json                la                   la   
72         ūma   AV  P224485.json           u₂-ma-a              u₂-ma-a   
73      annûri   AV  P224485.json         an-nu-rig            an-nu-rig   
76        ištu  PRP  P224485.json              TA@v               TA@v\m   
77        pānu    N  P224485.json             pa-an                pa-an   
79          lū  MOD  P224485.json                lu                   lu   
80          lā  MOD  P224485.json                la                  ⸢la   
86        mīnu   XP  P224485.json           mi-i-nu              mi-i-nu   
87          ša  REL  P224485.json                ša                ša\dd   
93          ša  REL  P224485.json                ša                   ša   
95          mā  PRP  P224485.json              ma-a                 ma-a   
96          kī  PRP  P224485.json              ki-i                 ki-i   
97          ša  REL  P224485.json                ša                   ša   
98          šū   IP  P224485.json             šu-u₂                šu-u₂   
100         ša  DET  P224485.json                ša                   ša   
101      šarru    N  P224485.json             LUGAL              ⸢LUGAL⸣   
102       bēlu    N  P224485.json         be-li₂-ia         

Create the text matrix with raw counts

In [12]:
df_ortho_wordstr = pd.DataFrame(df_ortho_words.groupby(['text_id']).apply(lambda x: ' '.join(x['lemma_norm_form'])))
df_ortho_wordstr.columns = ['ortho_wordstr']
df_ortho_str

cv = CountVectorizer(token_pattern='[^ ]+',lowercase=False)
ft = cv.fit_transform(list(df_ortho_wordstr['ortho_wordstr']))
tm_ortho_word = pd.DataFrame(ft.toarray(),columns=cv.get_feature_names(),index=df_ortho_wordstr.index)
tm_ortho_word.to_csv('output/tm_ortho_word.csv',encoding='utf-8',sep='\t')
tm_ortho_word

Urarṭaya[Urarṭian]EN:Urarṭaya:{KUR}URI-a.a  adanniš[very  \
text_id                                                             
P224485                                           0             2   
P237089                                           0             0   
P238649                                           0             0   
P313416                                           0             0   
P313417                                           0             0   
P313419                                           0             0   
P313420                                           0             0   
P313421                                           0             0   
P313422                                           0             0   
P313425                                           0             1   
P313427                                           0             0   
P313434                                           0             0   
P313435                                           0             0   
P313437                                           0             0   
P313439                                           0             0   
P313442                                           0             0   
P313444                                           0             1   
P313445                                           0             0   
P313447                                           0             0   
P313448                                           0             1   
P313450                                           0             0   
P313451                                           0             1   
P313452                                           1             0   
P313453                                           0             0   
P313454                                           0             0   
P313455                                           0             0   
P313457                                           0             0   
P313458                                           0             0   
P313462                                           0             0   
P313469                                           0             2   
...                                             ...           ...   
P336178                                           0             0   
P336595                                           0             0   
P336596                                           0             0   
P336597                                           0             0   
P336635                                           0             0   
P336636                                           0             0   
P336768                                           0             0   
P336769                                           0             0   
P336770                                           0             0   
P336771                                           0             0   
P336772                                           0             0   
P336773                                           0             0   
P336774                                           0             0   
P336775                                           0             0   
P336776                                           0             0   
P337150                                           0             0   
P337151                                           0             0   
P393855                                           0             0   
P393866                                           0             0   
X900004                                           0             0   
X900005                                           0             0   
X900006                                           0             0   
X900007                                           0             0   
X900008                                           0             0   
X900009                                           3             2   
X900010

Put them all together

In [13]:
tm_counts = pd.concat([tm_paleo,tm_ortho_sign,tm_ortho_word],axis=1)

<h3>Selecting the Features</h3>

<p>Three criteria are employed for selecting the initial list of features for clustering</p>
<ol>
    <li>Variations that have the highest frequency throughout the corpus</li>
    <li>Variations that are used in a mixed distribution rather than a complementary distribution. This criterion is only for the paleography and syllable variation, whose context is examined through the words they appear in. The form variations themselves thus cannot be examined in this context.</li>
    <li>Variations that look "good" based on an examination of the feature count matrices and their distrubtion within certain groups to be defined later</li>
</ol>
    Obviously, we cannot look at (3) right now but we can look at each of the first two for the three feature types.

<p>1.1 Paleography Frequencies</p>

In [14]:
df_paleo_count = pd.DataFrame(df_paleo.groupby(['sign_form','combined'])['cf'].agg('count'))
df_paleo_count = df_paleo_count[df_paleo_count[('cf')] > 100]

df_paleo_uniq = df_paleo_count.groupby([('sign_form')]).nunique()

df_paleo_count = df_paleo_count.loc[list(df_paleo_uniq[df_paleo_uniq[('cf')] > 1].index)]
df_paleo_count

cf
sign_form  combined            
BA         BA:..            401
           BA:.t.           120
BU         BU:..            960
           BU:.p.           109
DA         DA:..            434
           DA:.d.           201
DI         DI:..           1024
           DI:.d.           156
LI         LI:..            465
           LI:.d.           147
LU₂        LU₂:..           218
           LU₂:v..         1147
           LU₂:v.y.         500
NA         NA:..           2500
           NA:.t.           442
NI         NI:..           4666
           NI:.d.           281
RU         RU:..            444
           RU:.d.           108
SU         SU:..            245
           SU:.t.           116
TA         TA:..            960
           TA:.m.v          309
TI         TI:..            278
           TI:.t.           450
U₂         U₂:..           1302
           U₂:.m.           325
|ME.U.U.U| |ME.U.U.U|:..   1375
           |ME.U.U.U|:.m.   565
ŠA         ŠA:..           1082
           ŠA:.d.           263
           ŠA:.dm.          291
           ŠA:.m.           157
           ŠA:.y.           110
           ŠA:.yd.          124

<p>1.2 Syllable Frequencies</p>

In [15]:
df_ortho_sign_count = pd.DataFrame(df_ortho_signs.groupby(['str_part','b'])['cf'].agg('count'))
df_ortho_sign_count = df_ortho_sign_count[df_ortho_sign_count[('cf')] > 100]

df_ortho_sign_uniq = df_ortho_sign_count.groupby([('str_part')]).nunique()

df_ortho_sign_count = df_ortho_sign_count.loc[list(df_ortho_sign_uniq[df_ortho_sign_uniq[('cf')] > 1].index)]
df_ortho_sign_count

cf
str_part b        
aš       aš    392
         aš₂   427
ia       ia   1724
         ia₂   424
li       li    701
         li₂  1191
tu       tu    440
         tu₂   533
u        u    1503
         u₂   1843
         u₃    256
ša       ša   2827
         ša₂   439
šu       šu    747
         šu₂  1725

<p>1.3 Word Form Frequencies</p>

In [16]:
df_ortho_word_count = pd.DataFrame(df_words.groupby(['lemma_norm','lemma_norm_form'])['cf'].agg('count'))
df_ortho_word_count = df_ortho_word_count[df_ortho_word_count[('cf')] > 50]

df_ortho_word_uniq = df_ortho_word_count.groupby([('lemma_norm')]).nunique()

df_ortho_word_count = df_ortho_word_count.loc[list(df_ortho_word_uniq[df_ortho_word_uniq[('cf')] > 1].index)]
df_ortho_word_count

cf
lemma_norm                 lemma_norm_form                         
bēlu[lord]N:bēlī           bēlu[lord]N:bēlī:EN                  182
                           bēlu[lord]N:bēlī:be-li₂              642
bēlu[lord]N:bēlīya         bēlu[lord]N:bēlīya:EN-a               76
                           bēlu[lord]N:bēlīya:EN-ia             770
                           bēlu[lord]N:bēlīya:EN-ia₂            190
                           bēlu[lord]N:bēlīya:be-li₂-ia         309
                           bēlu[lord]N:bēlīya:be-li₂-ia₂        194
ištu[from]PRP:issu         ištu[from]PRP:issu:TA                113
                           ištu[from]PRP:issu:TA@v              346
libbu[interior]N:libbi     libbu[interior]N:libbi:ŠA₃           217
                           libbu[interior]N:libbi:ŠA₃-bi        277
lā[not]MOD:lā              lā[not]MOD:lā:la                     623
                           lā[not]MOD:lā:la-a                   117
lū[may]MOD:lū              lū[may]MOD:lū:lu                     516
                           lū[may]MOD:lū:lu-u                   190
muhhu[skull]N:muhhi        muhhu[skull]N:muhhi:UGU              681
                           muhhu[skull]N:muhhi:UGU-hi            56
mā[saying]PRP:mā           mā[saying]PRP:mā:ma                   61
                           mā[saying]PRP:mā:ma-a               1442
māru[son]N:mār             māru[son]N:mār:DUMU                   61
                           māru[son]N:mār:{LU₂}A-KIN             51
pānu[front]N:pān           pānu[front]N:pān:IGI                 142
                           pānu[front]N:pān:pa-an               146
šulmu[completeness]N:šulmu šulmu[completeness]N:šulmu:DI-mu     597
                           šulmu[completeness]N:šulmu:šul-mu     91
šū[he]IP:šû                šū[he]IP:šû:šu-u                      52
                           šū[he]IP:šû:šu-u₂                     81
ṣābu[people]N:ṣābāni       ṣābu[people]N:ṣābāni:ERIM-MEŠ         67
                           ṣābu[people]N:ṣābāni:{LU₂}ERIM-MEŠ   148

<p>2.1 Paleography Distrubtion within words

Now let's try to apply a quantitative method to figure out the level of mixed distribution which paleographic variants bear within word forms. The steps here are:
<ol>
    <li>Select only the particular sign forms and modifications that appear a sufficient number of times within the same forms</li>
    <li>Count the number of times these sign forms and modiciations occur in each text</li>
    <li>Create a text matrix which contains the appropriate distribution for the modifications within each sign form, adding 1 to each cell to avoid divide by zero issues</li>
</ol>

In [68]:
df_mods_agg = pd.DataFrame(df_paleo.groupby(['sign_form','form','mods_str'])['a'].agg('count')).reset_index()
df_mods_agg.columns = ['sign_form','form','mods_str','count']
#first let's remove where total instances are less than a certain arbitrary value, say 5
df_mods_agg = df_mods_agg[df_mods_agg['count'] >= 5]
#NOW find and only keep the rows where sign_form and form are duplicates
df_mods_agg['is_dup'] = df_mods_agg.duplicated(['sign_form','form'],False)
df_mods_agg = df_mods_agg[df_mods_agg['is_dup'] == True]
df_mods_agg.to_csv('output/dist_paleo.csv',encoding='utf-8')
df_mods_agg

sign_form                  form mods_str  count  is_dup
1894            ANŠE                  ANŠE       ..     26    True
1895            ANŠE                  ANŠE      .d.      7    True
1919            ANŠE      {ANŠE}KUR.RA-MEŠ       ..     32    True
1920            ANŠE      {ANŠE}KUR.RA-MEŠ      .d.     13    True
1988            ARAD               ARAD-ka       ..    426    True
1990            ARAD               ARAD-ka      .p.     17    True
2007            ARAD         {LU₂}ARAD-MEŠ       ..     27    True
2008            ARAD         {LU₂}ARAD-MEŠ      .p.      5    True
2273              BA              e-tar-ba       ..     14    True
2274              BA              e-tar-ba      .t.      5    True
2278              BA           i-ba-aš₂-ši       ..     28    True
2279              BA           i-ba-aš₂-ši      .t.     11    True
2288              BA               i-ba-ši       ..     26    True
2290              BA               i-ba-ši      .t.      6    True
3163              BU                gab-bu       ..     68    True
3164              BU                gab-bu      .p.      6    True
3165              BU                gab-bu      .t.      5    True
3339              BU             lik-ru-bu       ..     46    True
3340              BU             lik-ru-bu      .t.      5    True
3584              BU                ŠA₃-bu       ..     32    True
3586              BU                ŠA₃-bu      .t.      6    True
3933              DA                 u₂-da       ..     39    True
3934              DA                 u₂-da      .d.     21    True
3961              DA    {1}DINGIR-ia-da-aʾ       ..     19    True
3962              DA    {1}DINGIR-ia-da-aʾ      .d.      5    True
4088              DI                 DI-mu       ..    497    True
4089              DI                 DI-mu      .d.     53    True
4100              DI                  a-di       ..     62    True
4101              DI                  a-di      .d.     13    True
4156              DI              di-ib-bi       ..     19    True
4157              DI              di-ib-bi      .d.      6    True
4326              DI              u₂-di-ni       ..     14    True
4327              DI              u₂-di-ni      .d.      5    True
5360              E₂                    E₂       ..    117    True
5361              E₂                    E₂      .d.      8    True
8062              IG           iq-ṭi₂-bi-a       ..     17    True
8063              IG           iq-ṭi₂-bi-a      .d.      6    True
8867              IŠ          iš-pur-an-ni       ..    220    True
8868              IŠ          iš-pur-an-ni      .d.     12    True
8869              IŠ          iš-pur-an-ni      .t.     21    True
9440             KAL             a-dan-niš       ..    114    True
9441             KAL             a-dan-niš      .d.      5    True
10111            KIN            {LU₂}A-KIN       ..     70    True
10113            KIN            {LU₂}A-KIN      .t.      8    True
11049             LA                    la       ..    532    True
11053             LA                    la      .p.     10    True
11503             LI             le-pu-šu₂       ..      9    True
11504             LI             le-pu-šu₂      .d.      6    True
11634             LI             lil-li-ka       ..     16    True
11635             LI             lil-li-ka      .d.      6    True
11815            LIŠ                liš-al       ..      7    True
11816            LIŠ                liš-al      .d.      5    True
11843            LIŠ             liš-pu-ra       ..     16    True
11844            LIŠ             liš-pu-ra      .d.      9    True
12220          LUGAL                 LUGAL       ..   2167    True
12221          LUGAL                 LUGAL      .d.     68    True
12223          LUGAL                 LUGAL      .m.      6    True
12224          LUGAL                 LUGAL      .p.     48    True
12226          LUGAL                 LUGAL      .t.     63

In [61]:
df_select_signmods = df_mods_agg[['sign_form','mods_str']].drop_duplicates()
df_select_signmods['combined'] = df_select_signmods['sign_form'] + ':' + df_select_signmods['mods_str']
df_select_signmods

sign_form mods_str           combined
1894            ANŠE       ..            ANŠE:..
1895            ANŠE      .d.           ANŠE:.d.
1988            ARAD       ..            ARAD:..
1990            ARAD      .p.           ARAD:.p.
2273              BA       ..              BA:..
2274              BA      .t.             BA:.t.
3163              BU       ..              BU:..
3164              BU      .p.             BU:.p.
3165              BU      .t.             BU:.t.
3933              DA       ..              DA:..
3934              DA      .d.             DA:.d.
4088              DI       ..              DI:..
4089              DI      .d.             DI:.d.
5360              E₂       ..              E₂:..
5361              E₂      .d.             E₂:.d.
8062              IG       ..              IG:..
8063              IG      .d.             IG:.d.
8867              IŠ       ..              IŠ:..
8868              IŠ      .d.             IŠ:.d.
8869              IŠ      .t.             IŠ:.t.
9440             KAL       ..             KAL:..
9441             KAL      .d.            KAL:.d.
10111            KIN       ..             KIN:..
10113            KIN      .t.            KIN:.t.
11049             LA       ..              LA:..
11053             LA      .p.             LA:.p.
11503             LI       ..              LI:..
11504             LI      .d.             LI:.d.
11815            LIŠ       ..             LIŠ:..
11816            LIŠ      .d.            LIŠ:.d.
12220          LUGAL       ..           LUGAL:..
12221          LUGAL      .d.          LUGAL:.d.
12223          LUGAL      .m.          LUGAL:.m.
12224          LUGAL      .p.          LUGAL:.p.
12226          LUGAL      .t.          LUGAL:.t.
12229          LUGAL      .y.          LUGAL:.y.
12326            LU₂      v..            LU₂:v..
12327            LU₂     v.y.           LU₂:v.y.
12465            LU₂       ..             LU₂:..
13234             MA       ..              MA:..
13237             MA      .p.             MA:.p.
13981             MU       ..              MU:..
13983             MU      .p.             MU:.p.
14335             NA       ..              NA:..
14336             NA      .t.             NA:.t.
14351             NA      .d.             NA:.d.
14352             NA     .dt.            NA:.dt.
14354             NA     .td.            NA:.td.
14355             NA      .y.             NA:.y.
14947            NAM       ..             NAM:..
14949            NAM      .p.            NAM:.p.
15246             NI       ..              NI:..
15247             NI      .d.             NI:.d.
17791            NUN       ..             NUN:..
17792            NUN     .dm.           NUN:.dm.
17793            NUN      .m.            NUN:.m.
20015          SILA₃       ..           SILA₃:..
20016          SILA₃      .d.          SILA₃:.d.
20193             SU       ..              SU:..
20194             SU      .t.             SU:.t.
20397            SUM       ..             SUM:..
20398            SUM      .m.            SUM:.m.
20399            SUM      .p.            SUM:.p.
20494             TA       ..              TA:..
20497             TA      .m.             TA:.m.
20498             TA      .p.             TA:.p.
20499             TA      ..v             TA:..v
20500             TA    .dm.v           TA:.dm.v
20501             TA     .m.v            TA:.m.v
20502             TA    .mp.v           TA:.mp.v
20504             TA     .p.v            TA:.p.v
21677             TI       ..              TI:..
21678             TI      .t.             TI:.t.
23335            URI       ..             URI:..
23336            URI      .d.            URI:.d.
23337            URI     .dd.           URI:.dd.
23338            URI     .dm.           URI:.dm.
23452            URU       ..             URU:..
23453            URU      .d.            URU:.d.
23912             U₂       ..              U₂:..
23913             U₂      .m.             

<p>2.2 Same for Syllable Orthography</p>

In [27]:
df_ortho_signs['form_str_part'] = df_ortho_signs['form'].apply(lambda x: re.sub(r'[₁₂₃₄₅₆₇₈₉₀]','',x))
df_ortho_signs

C:\Users\jason\Anaconda3\lib\site-packages\ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  """Entry point for launching an IPython kernel.


a     b    break                cf     epos f           file  \
0            a  damaged             awātu        N     P224485.json   
3            a                        ana      PRP     P224485.json   
6           aš           Aššur-šarru-uṣur       PN     P224485.json   
12          ia                      yâšim       IP     P224485.json   
13           a  damaged             yâšim       IP     P224485.json   
17           a                        ana      PRP     P224485.json   
20          aš                  Mat-Aššur       GN     P224485.json   
24          ka  missing             libbu        N     P224485.json   
28          ka                       ṭābu       AJ     P224485.json   
29          ša  damaged                ša      REL     P224485.json   
35           a                         mā      PRP     P224485.json   
40          ša  missing                ša      DET     P224485.json   
42          me                       Mita       PN     P224485.json   
44           a                       Mita       PN     P224485.json   
47          ka                    Muskaya       EN     P224485.json   
48           a                    Muskaya       EN     P224485.json   
49           a                    Muskaya       EN     P224485.json   
53          ia                      muhhu        N     P224485.json   
56          ka                      alāku        V     P224485.json   
58           a                         mā      PRP     P224485.json   
64           u                     Quwaya       EN     P224485.json   
65           a                     Quwaya       EN     P224485.json   
66           a  damaged            Quwaya       EN     P224485.json   
67          ša  damaged                ša      REL     P224485.json   
69          u₂  damaged              Urik       PN     P224485.json   
72           a                        ana      PRP     P224485.json   
78           a                        ana      PRP     P224485.json   
82          u₂                     wabālu        V     P224485.json   
86           u                     wabālu        V     P224485.json   
89           a                         mā      PRP     P224485.json   
...    ..  ...      ...               ...      ... ..           ...   
154955      ku                      anāku       IP     X900015.json   
154956      ša                         ša      REL     X900015.json   
154958      be                       bēlu        N     X900015.json   
154959     li₂                       bēlu        N     X900015.json   
154965       a                         mā      PRP     X900015.json   
154972       i                       išti      PRP     X900015.json   
154974      ka                       išti      PRP     X900015.json   
154976      li                      alāku        V     X900015.json   
154977      ku  damaged             alāku        V     X900015.json   
154981      tu                      hubtu        N     X900015.json   
154982       a                   adakanni       AV     X900015.json   
154983      da  damaged          adakanni       AV     X900015.json   
154984      ka  damaged          adakanni       AV     X900015.json   
154986       i  damaged             no-cf  no-epos     X900015.json   
155010     šu₂                       pānu        N     X900015.json   
155013       a  damaged                mā      PRP     X900015.json   
155017       a                         lā      MOD     X900015.json   
155019      ku                      alāku        V     X900015.json   
155027      qi                       leqû        V     X900015.json   
155030     kal                      kallû        N     X900015.json   
155031      li                      kallû        N     X900015.json   
155032      u₂                      kallû        N     X900015.json   
155033      ša                         ša      DET     X900015.json   
155035      aš           Aššur-daʾʾinanni       PN     X900015.json   
155040      ša                 

In [70]:
df_syls_agg = pd.DataFrame(df_ortho_signs.groupby(['str_part','form_str_part','b'])['a'].agg('count')).reset_index()
df_syls_agg.columns = ['str_part','form_str_part','b','count']
#first let's remove where total instances are less than a certain arbitrary value, say 5
df_syls_agg = df_syls_agg[df_syls_agg['count'] >= 3]
#NOW find and only keep the rows where sign_form and form are duplicates
df_syls_agg['is_dup'] = df_syls_agg.duplicated(['str_part','form_str_part'],False)
df_syls_agg = df_syls_agg[df_syls_agg['is_dup'] == True]
df_syls_agg.to_csv('output/dist_ortho_sign.csv',encoding='utf-8')
df_syls_agg

str_part       form_str_part     b  count  is_dup
1349       ar              ar-hiš    ar      3    True
1350       ar              ar-hiš   ar₂     28    True
2362      dul              dul-li   dul     20    True
2363      dul              dul-li  dul₆      4    True
2369      dul              dul-lu   dul     70    True
2370      dul              dul-lu  dul₆     31    True
2394      gir            e-gir-te   gir      3    True
2395      gir            e-gir-te  gir₂      8    True
2402      gir            e-gir-tu   gir      3    True
2403      gir            e-gir-tu  gir₂     36    True
2418      gur            i-ma-gur   gur      5    True
2419      gur            i-ma-gur  gur₂     11    True
3248       ia               BE-ia    ia     11    True
3249       ia               BE-ia   ia₂      9    True
3264       ia               EN-ia    ia    770    True
3265       ia               EN-ia   ia₂    190    True
3280       ia           UGU-hi-ia    ia     74    True
3281       ia           UGU-hi-ia   ia₂      7    True
3294       ia            be-li-ia    ia    310    True
3295       ia            be-li-ia   ia₂    196    True
3341       ia            pa-ni-ia    ia     56    True
3342       ia            pa-ni-ia   ia₂      5    True
3427       ia        {LU}A-KIN-ia    ia     45    True
3428       ia        {LU}A-KIN-ia   ia₂      3    True
4575       li               EN-li    li     14    True
4576       li               EN-li   li₂      4    True
4591       li               be-li    li     19    True
4592       li               be-li   li₂    645    True
4596       li            be-li-ia    li      3    True
4597       li            be-li-ia   li₂    503    True
5198       mi             mi-i-nu    mi     61    True
5199       mi             mi-i-nu   mi₃     14    True
5210       mi               mi-ni    mi      7    True
5211       mi               mi-ni   mi₃      8    True
5215       mi               mi-nu    mi     40    True
5216       mi               mi-nu   mi₃     13    True
5439       tu            an-ni-tu    tu      4    True
5440       tu            an-ni-tu   tu₂     27    True
5446       tu            at-tu-nu    tu     18    True
5447       tu            at-tu-nu   tu₂      6    True
5481       tu            hu-ub-tu    tu      3    True
5482       tu            hu-ub-tu   tu₂      4    True
5543       tu           ia-mut-tu    tu      3    True
5544       tu           ia-mut-tu   tu₂      3    True
5646       tu            ma-da-tu    tu      4    True
5647       tu            ma-da-tu   tu₂      9    True
5716       tu           pu-tu-u-a    tu      3    True
5717       tu           pu-tu-u-a   tu₂      5    True
5738       tu                  tu    tu      6    True
5739       tu                  tu   tu₂     14    True
5835       tu                x-tu    tu      3    True
5836       tu                x-tu   tu₂     13    True
5879       tu        {LU}hu-ub-tu    tu      3    True
5880       tu        {LU}hu-ub-tu   tu₂      7    True
5888       tu     {LU}i-tu-ʾa-a.a    tu     10    True
5889       tu     {LU}i-tu-ʾa-a.a   tu₂      3    True
5945       tu               šu-tu    tu      5    True
5946       tu               šu-tu   tu₂     15    True
5952       tu          šu-tu-u-ni    tu      3    True
5953       tu          šu-tu-u-ni   tu₂      3    True
5954       tu             šu-u-tu    tu      3    True
5955       tu             šu-u-tu   tu₂     25    True
5966        u                02-u     u      5    True
5967        u                02-u    u₂      3    True
6056        u             an-ni-u     u     14    True
6057        u             an-ni-u    u₂     34    True
6192        u        i-qa-bu-u-ni     u     20    True
6193        u        i-qa-bu-u-ni    u₂      3    True
6277        u         il-lak-u-ni     u     14    True
6278        u         il-lak-u-ni    u₂      3    True
6282        u         il-lik-u-ni     u     22    True
6283        u         il-lik-u-ni    u₂      

In [63]:
df_select_bs = df_syls_agg[['str_part','b']].drop_duplicates()
#Don't need to create combined column here because b is sufficient
#df_select_signmods['combined'] = df_select_signmods['sign_form'] + ':' + df_select_signmods['mods_str']
df_select_bs

str_part     b
1349       ar    ar
1350       ar   ar₂
2362      dul   dul
2363      dul  dul₆
2394      gir   gir
2395      gir  gir₂
2418      gur   gur
2419      gur  gur₂
3248       ia    ia
3249       ia   ia₂
4575       li    li
4576       li   li₂
5198       mi    mi
5199       mi   mi₃
5439       tu    tu
5440       tu   tu₂
5966        u     u
5967        u    u₂
6587        u    u₃
7716       ša    ša
7717       ša   ša₂
8027       šu    šu
8028       šu   šu₂
8995      šum   šum
8996      šum  šum₂
9010       ṭe    ṭe
9011       ṭe   ṭe₃
9062       ṭi    ṭi
9063       ṭi   ṭi₂

In [30]:
select_syls = list(df_syls_agg['str_part'].unique())
select_syls

['dul', 'gur', 'ia', 'li', 'mi', 'tu', 'u', 'ša', 'šu', 'šum', 'ṭi']

In [31]:
df_file_select_bs = df_ortho_signs[df_ortho_signs['str_part'].isin(select_syls)]
df_file_select_bs = pd.DataFrame(df_file_select_bs.groupby(['file','str_part','b'])['a'].agg('count')).reset_index()
#Again combined is just b
#df_file_select_syls['combined'] = df_file_select_signs['sign_form'] + ':' + df_file_select_signs['mods_str']
df_file_select_bs

file str_part     b   a
0     P224485.json      dul   dul   2
1     P224485.json       ia    ia  16
2     P224485.json       li    li   6
3     P224485.json       li   li₂   7
4     P224485.json       mi    mi   7
5     P224485.json       mi   mi₃   1
6     P224485.json       tu    tu  10
7     P224485.json       tu   tu₂   6
8     P224485.json        u     u   9
9     P224485.json        u    u₂  19
10    P224485.json       ša    ša  21
11    P224485.json       ša   ša₂   5
12    P224485.json       šu    šu   4
13    P224485.json       šu   šu₂  33
14    P224485.json      šum   šum   1
15    P237089.json      dul  dul₆   1
16    P237089.json       ia   ia₂   3
17    P237089.json       li    li   1
18    P237089.json       li   li₂   2
19    P237089.json       tu   tu₂   1
20    P237089.json        u     u   2
21    P237089.json       ša    ša   3
22    P237089.json       šu    šu   1
23    P238649.json       li    li   1
24    P238649.json        u     u   1
25    P238649.json        u    u₂   1
26    P238649.json       ša    ša   2
27    P313416.json       ia    ia   1
28    P313416.json       ia   ia₂   2
29    P313416.json       li   li₂   3
...            ...      ...   ...  ..
6233  X900012.json       tu   tu₂   2
6234  X900012.json        u     u   5
6235  X900012.json        u    u₂   6
6236  X900012.json        u    u₃   4
6237  X900012.json       ša    ša  13
6238  X900012.json       šu    šu   1
6239  X900012.json       šu   šu₂  11
6240  X900012.json      šum  šum₂   1
6241  X900012.json       ṭi   ṭi₂   1
6242  X900014.json      dul   dul   2
6243  X900014.json       ia    ia   5
6244  X900014.json       li    li   1
6245  X900014.json       li   li₂   2
6246  X900014.json       tu    tu   4
6247  X900014.json        u     u   4
6248  X900014.json        u    u₂   6
6249  X900014.json       ša    ša   8
6250  X900014.json       šu   šu₂   6
6251  X900015.json       ia    ia   1
6252  X900015.json       ia   ia₂   3
6253  X900015.json       li    li   2
6254  X900015.json       li   li₂   5
6255  X900015.json       mi    mi   1
6256  X900015.json       tu    tu   1
6257  X900015.json       tu   tu₂   2
6258  X900015.json        u     u   3
6259  X900015.json        u    u₂   4
6260  X900015.json       ša    ša  10
6261  X900015.json       šu   šu₂   1
6262  X900015.json      šum   šum   2

[6263 rows x 4 columns]

<p>3. Defining our selection</p>

In [66]:
#Paleography
map_paleo = {'BA':['BA:..','BA:.t.'],
            'BU':['BU:..','BU:.p.'],
            'DA':['DA:..','DA:.d.'],
             'DI':['DI:..','DI:.d.'],
             'LI':['LI:..','LI:.d.'],
             'LU₂':['LU₂:v..','LU₂:v.y.'],
             'NA':['NA:..','NA:.t.'],
             'NI':['NI:..','NI:.d.'],
            'SU':['SU:..','SU:.t.'],
            'TI':['TI:..','TI:.t.'],
            'U₂':['U₂:..','U₂:.m.'],
             #'RU':['RU:..','RU:.d.'],
             '|ME.U.U.U|':['|ME.U.U.U|:..','|ME.U.U.U|:.m.'],
             'ŠA': ['ŠA:..','ŠA:.dm.']
            }
list_paleo = []
list_paleo_pairs = []
for v in map_paleo.values():
    list_paleo = list_paleo + v
    list_paleo_pairs.append(v)
list_paleo

#Orthography - Sign
map_ortho_sign = {'ia':['ia','ia₂'],
                  'li':['li','li₂'],
                  'ša':['ša','ša₂'],
                  'šu':['šu','šu₂'],
                  'tu':['tu','tu₂'],
                  'u':['u','u₂']
                 }
list_ortho_sign = []
list_ortho_sign_pairs = []
for v in map_ortho_sign.values():
    list_ortho_sign = list_ortho_sign + v
    list_ortho_sign_pairs.append(v)
list_ortho_sign

#Orthography - Word
map_ortho_word = {'bēlu[lord]N:bēlī':['bēlu[lord]N:bēlī:be-li₂','bēlu[lord]N:bēlī:EN'],
                  'bēlu[lord]N:bēlīya':['bēlu[lord]N:bēlīya:EN-ia','bēlu[lord]N:bēlīya:be-li₂-ia'],
                  'libbu[interior]N:libbi':['libbu[interior]N:libbi:ŠA₃','libbu[interior]N:libbi:ŠA₃-bi'],
                  'lā[not]MOD:lā':['lā[not]MOD:lā:la','lā[not]MOD:lā:la-a'],
                  'lū[may]MOD:lū':['lū[may]MOD:lū:lu','lū[may]MOD:lū:lu-u'],
                  'mā[saying]PRP:mā':['mā[saying]PRP:mā:ma','mā[saying]PRP:mā:ma-a'],
                  'muhhu[skull]N:muhhi':['muhhu[skull]N:muhhi:UGU','muhhu[skull]N:muhhi:UGU-hi'],
                  'pānu[front]N:pān':['pānu[front]N:pān:IGI','pānu[front]N:pān:pa-an'],
                  'šulmu[completeness]N:šulmu':['šulmu[completeness]N:šulmu:DI-mu','šulmu[completeness]N:šulmu:šul-mu']
                }
list_ortho_word = []
list_ortho_word_pairs = []
for v in map_ortho_word.values():
    list_ortho_word = list_ortho_word + v
    list_ortho_word_pairs.append(v)
list_ortho_word_pairs
list_features_all = list_paleo + list_ortho_sign + list_ortho_word
list_pairs_all = list_paleo_pairs + list_ortho_sign_pairs + list_ortho_word_pairs

Save the counts matrices with only these features

In [80]:
tm_counts_class = pd.concat([tm_counts[list_features_all],df_class],axis=1)
tm_counts_class.to_csv('output/tm_counts.csv',encoding='utf-8')

tm_counts_class_senderloc = pd.DataFrame(tm_counts_class.groupby('senderloc').agg('sum'))[list_features_all]
tm_counts_class_senderloc.to_csv('output/tm_counts_senderloc.csv',encoding='utf-8')

tm_counts_class_dossier = pd.DataFrame(tm_counts_class.groupby('dossier_nocertain').agg('sum'))[list_features_all]
tm_counts_class_dossier.to_csv('output/tm_counts_dossier.csv',encoding='utf-8')

tm_counts_class_dossier = pd.DataFrame(tm_counts_class.groupby('dossier').agg('sum'))[list_features_all]
tm_counts_class_dossier.to_csv('output/tm_counts_dossier_abc.csv',encoding='utf-8')

tm_counts_class_saachap = pd.DataFrame(tm_counts_class.groupby('saa_chap').agg('sum'))[list_features_all]
tm_counts_class_saachap.to_csv('output/tm_counts_saachap.csv',encoding='utf-8')

Put them all together

In [33]:
map_all = map_paleo.copy()
map_all.update(map_ortho_sign)
map_all.update(map_ortho_word)
map_all

{'NA': ['NA:..', 'NA:.t.'],
 'NI': ['NI:..', 'NI:.d.'],
 'bēlu[lord]N:bēlīya': ['bēlu[lord]N:bēlīya:EN-ia',
  'bēlu[lord]N:bēlīya:be-li₂-ia'],
 'ia': ['ia', 'ia₂'],
 'lā[not]MOD:lā': ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a'],
 'lū[may]MOD:lū': ['lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u'],
 'u': ['u', 'u₂'],
 '|ME.U.U.U|': ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.'],
 'ša': ['ša', 'ša₂'],
 'šu': ['šu', 'šu₂']}

Form the Power Set

In [82]:
def p(s):
    powerset = []
    for i in range(2**len(s)):
        subset = [x for j,x in enumerate(s) if (i >> j) & 1]
        powerset.append(subset)
    return powerset

In [83]:
import itertools
list_power = p(list_pairs_all)
list_power = [list(itertools.chain.from_iterable(x)) for x in list_power if x != []]
len(list_power)

KeyboardInterrupt: 

Form the distribution matrix

In [84]:
df_form_count = pd.DataFrame(df_words[df_words['lemma_norm_form'].isin(list_ortho_word)].groupby(['lemma_norm','lemma_norm_form'])['cf'].agg('count'))
df_form_count

dict_form_count = {}
for ln in map_ortho_word:
    count1 = float(df_form_count.loc[(ln,map_ortho_word[ln][0])]['cf'])
    count2 = float(df_form_count.loc[(ln,map_ortho_word[ln][1])]['cf'])
    tot12 = count1 + count2
    dict_form_count[map_ortho_word[ln][0]] = count1 / tot12
    dict_form_count[map_ortho_word[ln][1]] = count2 / tot12
dict_form_count

df_paleo_count = pd.DataFrame(df[df['combined'].isin(list_paleo)].groupby(['sign_form','combined'])['cf'].agg('count'))
df_paleo_count

dict_paleo_count = {}
for ln in map_paleo:
    count1 = float(df_paleo_count.loc[(ln,map_paleo[ln][0])]['cf'])
    count2 = float(df_paleo_count.loc[(ln,map_paleo[ln][1])]['cf'])
    tot12 = count1 + count2
    dict_paleo_count[map_paleo[ln][0]] = count1 / tot12
    dict_paleo_count[map_paleo[ln][1]] = count2 / tot12
dict_paleo_count

df_sign_count = pd.DataFrame(df[df['b'].isin(list_ortho_sign)].groupby(['str_part','b'])['cf'].agg('count'))
df_sign_count

dict_sign_count = {}
for ln in map_ortho_sign:
    count1 = float(df_sign_count.loc[(ln,map_ortho_sign[ln][0])]['cf'])
    count2 = float(df_sign_count.loc[(ln,map_ortho_sign[ln][1])]['cf'])
    tot12 = count1 + count2
    dict_sign_count[map_ortho_sign[ln][0]] = count1 / tot12
    dict_sign_count[map_ortho_sign[ln][1]] = count2 / tot12
dict_sign_count

{'ia': 0.8026070763500931,
 'ia₂': 0.1973929236499069,
 'li': 0.370507399577167,
 'li₂': 0.629492600422833,
 'tu': 0.4522096608427544,
 'tu₂': 0.5477903391572456,
 'u': 0.4491930663478781,
 'u₂': 0.550806933652122,
 'ša': 0.8655848132271893,
 'ša₂': 0.13441518677281078,
 'šu': 0.30218446601941745,
 'šu₂': 0.6978155339805825}

In [85]:
dict_count_all = dict_paleo_count.copy()
dict_count_all.update(dict_sign_count)
dict_count_all.update(dict_form_count)
dict_count_all

{'BA:..': 0.7768166089965398,
 'BA:.t.': 0.2231833910034602,
 'BU:..': 0.9074852817493693,
 'BU:.p.': 0.09251471825063078,
 'DA:..': 0.7073825503355705,
 'DA:.d.': 0.29261744966442954,
 'DI:..': 0.8773946360153256,
 'DI:.d.': 0.12260536398467432,
 'LI:..': 0.7777777777777778,
 'LI:.d.': 0.2222222222222222,
 'LU₂:v..': 0.7032608695652174,
 'LU₂:v.y.': 0.2967391304347826,
 'NA:..': 0.8526540573520439,
 'NA:.t.': 0.14734594264795606,
 'NI:..': 0.9462425595238095,
 'NI:.d.': 0.05375744047619048,
 'SU:..': 0.6962962962962963,
 'SU:.t.': 0.3037037037037037,
 'TI:..': 0.42098765432098767,
 'TI:.t.': 0.5790123456790124,
 'U₂:..': 0.8165038002171553,
 'U₂:.m.': 0.18349619978284473,
 'bēlu[lord]N:bēlī:EN': 0.220873786407767,
 'bēlu[lord]N:bēlī:be-li₂': 0.779126213592233,
 'bēlu[lord]N:bēlīya:EN-ia': 0.7136237256719185,
 'bēlu[lord]N:bēlīya:be-li₂-ia': 0.28637627432808155,
 'ia': 0.8026070763500931,
 'ia₂': 0.1973929236499069,
 'li': 0.370507399577167,
 'libbu[interior]N:libbi:ŠA₃': 0.43927125506

Form the Distribution Matrix

In [40]:
def form_dist_matrix(tm_count,mapping):
    d = {}
    vecs = {}
    
    listing = []
    for v in mapping.values():
        listing = listing + v
        
    tm_count = tm_count[listing]
    for i, row in tm_count.iterrows():
        d[i] = {}
        for key in mapping:
            key_sum = np.sum(tm_count.loc[i][mapping[key]])
            for v in mapping[key]:
                if key_sum > 0:
                    d[i][v] = tm_count.loc[i][v] / key_sum
                else:
                    d[i][v] = np.nan

    tm_dist = pd.DataFrame(d).transpose()
    return tm_dist

In [41]:
tm_dist_all = form_dist_matrix(tm_counts,map_all)
tm_dist_all

NA:..    NA:.t.     NI:..    NI:.d.  bēlu[lord]N:bēlīya:EN-ia  \
P224485  0.526316  0.473684  0.977273  0.022727                  0.000000   
P237089  1.000000  0.000000  1.000000  0.000000                       NaN   
P238649  1.000000  0.000000  0.600000  0.400000                       NaN   
P313416  1.000000  0.000000  0.500000  0.500000                  0.000000   
P313417  0.357143  0.642857  1.000000  0.000000                  1.000000   
P313419  0.833333  0.166667  0.800000  0.200000                  1.000000   
P313420  1.000000  0.000000  1.000000  0.000000                       NaN   
P313421  1.000000  0.000000  1.000000  0.000000                  0.000000   
P313422  0.000000  1.000000  1.000000  0.000000                  1.000000   
P313425  0.769231  0.230769  1.000000  0.000000                  1.000000   
P313427  1.000000  0.000000  1.000000  0.000000                       NaN   
P313434  0.750000  0.250000  1.000000  0.000000                       NaN   
P313435  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313437  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313439  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313442  0.000000  1.000000  0.875000  0.125000                  1.000000   
P313444  1.000000  0.000000  1.000000  0.000000                       NaN   
P313445  1.000000  0.000000  1.000000  0.000000                       NaN   
P313447  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313448  1.000000  0.000000  1.000000  0.000000                  0.000000   
P313450  0.333333  0.666667  1.000000  0.000000                  1.000000   
P313451  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313452  1.000000  0.000000  0.909091  0.090909                  0.500000   
P313453  1.000000  0.000000  0.625000  0.375000                  1.000000   
P313454  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313455  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313457       NaN       NaN  0.600000  0.400000                  0.666667   
P313458  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313462  1.000000  0.000000  1.000000  0.000000                  0.000000   
P313469       NaN       NaN  0.666667  0.333333                       NaN   
...           ...       ...       ...       ...                       ...   
P336178  1.000000  0.000000  1.000000  0.000000                  1.000000   
P336595  1.000000  0.000000  1.000000  0.000000                       NaN   
P336596  1.000000  0.000000  1.000000  0.000000                  1.000000   
P336597  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336635       NaN       NaN  1.000000  0.000000                       NaN   
P336636  1.000000  0.000000       NaN       NaN                       NaN   
P336768  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336769  1.000000  0.000000  1.000000  0.000000                       NaN   
P336770  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336771  1.000000  0.000000  1.000000  0.000000                       NaN   
P336772       NaN       NaN  1.000000  0.000000                       NaN   
P336773       NaN       NaN       NaN       NaN                       NaN   
P336774  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336775       NaN       NaN       NaN       NaN                       NaN   
P336776  1.000000  0.000000  1.000000  0.000000                       NaN   
P337150  0.857143  0.142857  0.666667  0.333333                  0.000000   
P337151  1.000000  0.000000  1.000000  0.000000                       NaN   
P393855  1.000000  0.000000  1.000000  0.000000                  1.000000   
P393866  0.750000  0.250000  1.000000  0.000000                  0.000000   
X900004  1.000000  0.000000  1.000000  0.000000                  0.500000   
X900005 

Fill in empty features with their distribution over the entire corpus

In [42]:
for lnf in dict_count_all:
    #print(dict_form_count[lnf])
    tm_dist_all[lnf] = tm_dist_all[lnf].fillna(dict_count_all[lnf])
tm_dist_all

NA:..    NA:.t.     NI:..    NI:.d.  bēlu[lord]N:bēlīya:EN-ia  \
P224485  0.526316  0.473684  0.977273  0.022727                  0.000000   
P237089  1.000000  0.000000  1.000000  0.000000                  0.713624   
P238649  1.000000  0.000000  0.600000  0.400000                  0.713624   
P313416  1.000000  0.000000  0.500000  0.500000                  0.000000   
P313417  0.357143  0.642857  1.000000  0.000000                  1.000000   
P313419  0.833333  0.166667  0.800000  0.200000                  1.000000   
P313420  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313421  1.000000  0.000000  1.000000  0.000000                  0.000000   
P313422  0.000000  1.000000  1.000000  0.000000                  1.000000   
P313425  0.769231  0.230769  1.000000  0.000000                  1.000000   
P313427  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313434  0.750000  0.250000  1.000000  0.000000                  0.713624   
P313435  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313437  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313439  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313442  0.000000  1.000000  0.875000  0.125000                  1.000000   
P313444  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313445  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313447  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313448  1.000000  0.000000  1.000000  0.000000                  0.000000   
P313450  0.333333  0.666667  1.000000  0.000000                  1.000000   
P313451  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313452  1.000000  0.000000  0.909091  0.090909                  0.500000   
P313453  1.000000  0.000000  0.625000  0.375000                  1.000000   
P313454  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313455  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313457  0.852654  0.147346  0.600000  0.400000                  0.666667   
P313458  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313462  1.000000  0.000000  1.000000  0.000000                  0.000000   
P313469  0.852654  0.147346  0.666667  0.333333                  0.713624   
...           ...       ...       ...       ...                       ...   
P336178  1.000000  0.000000  1.000000  0.000000                  1.000000   
P336595  1.000000  0.000000  1.000000  0.000000                  0.713624   
P336596  1.000000  0.000000  1.000000  0.000000                  1.000000   
P336597  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336635  0.852654  0.147346  1.000000  0.000000                  0.713624   
P336636  1.000000  0.000000  0.946243  0.053757                  0.713624   
P336768  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336769  1.000000  0.000000  1.000000  0.000000                  0.713624   
P336770  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336771  1.000000  0.000000  1.000000  0.000000                  0.713624   
P336772  0.852654  0.147346  1.000000  0.000000                  0.713624   
P336773  0.852654  0.147346  0.946243  0.053757                  0.713624   
P336774  1.000000  0.000000  1.000000  0.000000                  0.500000   
P336775  0.852654  0.147346  0.946243  0.053757                  0.713624   
P336776  1.000000  0.000000  1.000000  0.000000                  0.713624   
P337150  0.857143  0.142857  0.666667  0.333333                  0.000000   
P337151  1.000000  0.000000  1.000000  0.000000                  0.713624   
P393855  1.000000  0.000000  1.000000  0.000000                  1.000000   
P393866  0.750000  0.250000  1.000000  0.000000                  0.000000   
X900004  1.000000  0.000000  1.000000  0.000000                  0.500000   
X900005 

<h3>Clustering</h3>

<p>In this section we iterate over each feature grouping in the power set to see which ones give us the best clustering. The measurements we are using are the Elbow Method and the Silhouette Score. These metrics can tell us how many clusters work best for each feature group, if any at all</p>

In [43]:
def calculate_scores(tm_dist,feature_list,flist_str):
    list_scores = []
    c = 0
    for g in feature_list:
        c += 1
        print(str(c) + '. Working on: ' + str(g))
        diff = 0
        decel = 0
        for k in range(1,30):
            d = {}
            km = KMeans(n_clusters=k,max_iter=1000).fit(tm_dist[g])

            sil_score = np.nan
            if k > 1:
                sil_score = silhouette_score(tm_dist[g],labels=km.labels_)

            if k > 2:
                decel = km.inertia_ - inertia  - diff
            if k > 1:
                diff = km.inertia_ - inertia

            inertia = km.inertia_

            d = {'group': str(g),'group_len': len(g), 'k': k,'sil_score': sil_score,'dist': inertia,'diff':diff,'decel':decel}
            list_scores.append(d)

    df_scores = pd.DataFrame(list_scores)
    df_scores.to_csv('output/scores_' + flist_str + '.csv',encoding='utf-8',sep='\t')
    return df_scores

In [44]:
def export_plots(df_scores,feature_list,flist_str):
    c = 0
    for g in feature_list:
        c += 1
        print(str(c) + '. Plotting: ' + str(g))
        df_temp = df_scores[df_scores['group'] == str(g)]
        K = list(df_temp['k'])

        plt.figure(figsize=(12, 12), dpi=120, facecolor='w', edgecolor='k')

        plt.plot(K,df_temp['dist'])
        plt.xticks(K)
        plt.xlabel('k')
        plt.ylabel('Distortion')
        plt.title('Elbow Method: ' + str(g))
        plt.savefig('output/plots/elbow_' + flist_str + '_reg_' + str(c) + '.png')

        plt.clf()

In [45]:
#df_scores = calculate_scores(tm_dist_all,list_ortho_word_power,'ortho_word')
#export_plots(df_scores,list_ortho_word_power,'ortho_word')
#df_scores = calculate_scores(tm_dist_all,list_ortho_sign_power,'ortho_sign')
#export_plots(df_scores,list_ortho_sign_power,'ortho_sign')
#df_scores = calculate_scores(tm_dist_all,list_paleo_power,'paleo')
#export_plots(df_scores,list_paleo_power,'paleo')

<h3>Evaluation</h3>
<p>For this section we will calculate purity scores for the clusters according to three types of classifications: Sender location, dossier, and SAA chapter</p>

In [46]:
cat_file = codecs.open('sargonletters/catalogue.json','r','utf-8')
cat_json = json.load(cat_file)

class_l = []
class_index = []
for pnum in cat_json['members']:
    id_text        = cat_json['members'][pnum].get('id_text','')
    designation    = cat_json['members'][pnum].get('designation','')
    ancient_author = cat_json['members'][pnum].get('ancient_author','')
    dossier        = cat_json['members'][pnum].get('dossier','')
    dossier_nocertain = '.'.join(dossier.split('.')[0:3])
    saa_chap       = '.'.join(dossier.split('.')[0:2])
    senderloc     = cat_json['members'][pnum].get('senderloc','')
    class_d = {'designation': designation,'ancient_author':ancient_author,'dossier':dossier,'dossier_nocertain': dossier_nocertain, 'senderloc':senderloc,'saa_chap':saa_chap}
    class_index.append(id_text)
    class_l.append(class_d)
    
df_class = pd.DataFrame(class_l,index=class_index)
df_class

ancient_author designation        dossier  \
P224485                  Sargon II  SAA 01 001  SAA01.01.01.a   
P237089                 Issar-duri  SAA 15 014  SAA15.01.01.a   
P238649                  (unknown)  SAA 15 368  SAA15.09.07.c   
P313416                 Sin-ašared  SAA 01 158  SAA01.07.15.c   
P313417        Mannu-ki-Aššur-le’i  SAA 01 233  SAA01.13.01.c   
P313419               [...]-ka’’in  SAA 05 040  SAA05.02.03.a   
P313420                   Il-yada’  SAA 15 164  SAA15.06.01.a   
P313421             Šarru-emuranni  SAA 15 237  SAA15.07.01.a   
P313422            Gabbu-ana-Aššur  SAA 05 114  SAA05.07.01.c   
P313425                  Bel-liqbi  SAA 01 179  SAA01.08.03.c   
P313427       Nabu-zer-ketti-lešir  SAA 01 152  SAA01.07.10.b   
P313434           Nabu-belu-ka’’in  SAA 15 025  SAA15.02.01.a   
P313435                 Nabu-pašir  SAA 01 192  SAA01.09.04.a   
P313437              Ṭab-šar-Aššur  SAA 01 062  SAA01.03.01.a   
P313439          Aššur-šumu-ka’’in  SAA 01 150  SAA01.07.08.a   
P313442                  (unknown)  SAA 15 074  SAA15.03.06.c   
P313444                   Il-yada’  SAA 15 172  SAA15.06.01.c   
P313445              Ṭab-šar-Aššur  SAA 05 290  SAA05.13.03.c   
P313447              Ṭab-šar-Aššur  SAA 01 056  SAA01.03.01.a   
P313448           Aššur-dur-paniya  SAA 05 056  SAA05.04.01.a   
P313450            Gabbu-ana-Aššur  SAA 05 117  SAA05.07.01.c   
P313451                Sennacherib  SAA 05 281  SAA05.13.02.b   
P313452                  (unknown)  SAA 05 108  SAA05.06.03.c   
P313453            Ṭab-ṣill-Ešarra  SAA 05 291  SAA05.14.01.c   
P313454                  (unknown)  SAA 15 048  SAA15.02.02.c   
P313455                  Na’di-ilu  SAA 05 068  SAA05.04.02.b   
P313457               Aššur-reṣuwa  SAA 05 098  SAA05.06.01.c   
P313458                      Hunni  SAA 01 134  SAA01.07.01.c   
P313462                  (unknown)  SAA 05 250  SAA05.12.10.c   
P313469                  Hu-Teššub  SAA 05 044  SAA05.03.01.b   
...                            ...         ...            ...   
P336178                  Na’di-ilu  SAA 05 065  SAA05.04.02.a   
P336595                  Sargon II  SAA 01 027  SAA01.01.01.c   
P336596              Ṭab-šar-Aššur  SAA 01 060  SAA01.03.01.b   
P336597              Ṭab-šar-Aššur  SAA 01 073  SAA01.03.01.a   
P336635    Nashir-Bel (Liphur-Bel)  SAA 05 013  SAA05.01.01.c   
P336636               Aššur-reṣuwa  SAA 05 101  SAA05.06.01.c   
P336768           Nabu-šumu-iddina  SAA 15 137  SAA15.05.03.c   
P336769          Aššur-belu-taqqin  SAA 15 178  SAA15.06.02.c   
P336770                  (unknown)  SAA 15 343  SAA15.09.07.c   
P336771                  (unknown)  SAA 15 360  SAA15.09.07.c   
P336772                  (unknown)  SAA 15 387  SAA15.09.07.c   
P336773                  (unknown)  SAA 15 388  SAA15.09.07.c   
P336774                  (unknown)  SAA 15 389  SAA15.09.07.c   
P336775                  (unknown)  SAA 15 390  SAA15.09.07.c   
P336776                  (unknown)  SAA 15 391  SAA15.09.07.c   
P337150               Aššur-reṣuwa  SAA 05 100  SAA05.06.01.a   
P337151            Aššur-zeru-ibni  SAA 05 081  SAA05.05.03.a   
P393855                  (unknown)  SAA 01 251  SAA01.14.01.c   
P393866  (unknown), Nabu-dur-makie  SAA 01 210  SAA01.10.03.c   
X900004                      Mahde  SAA 05 074  SAA05.05.01.a   
X900005                  Adda-hati  SAA 01 175  SAA01.08.02.a   
X900006                  Sargon II  SAA 01 026  SAA01.01.01.a   
X900007                  Adda-hati  SAA 01 176  SAA01.08.02.a   
X900008                   Bel-duri  SAA 01 172  SAA01.08.01.c   
X900009                Sennacherib  SAA 01 032  SAA01.02.01.c   
X900010                Adad-issiya  SAA 05 215  SAA05.10.04.a   
X900011                   Bel-duri  SAA 01 171  SAA01.08.01.a   
X900012           Nabu-belu-ka’’in  SAA 15 084  SAA15.04.01.c   
X900014             Marduk-remanni  SAA 01 110  SAA01.05.01.c   
X900015           Nabu-belu-ka’’in  SAA 15 083  SAA15.0

---PNUM DOSSIER---

In [86]:
def pnum_to_dossier(pnum):
    return df_class.loc[pnum]['dossier']

In [101]:
df['dossier'] = df['text_id'].apply(pnum_to_dossier)

In [399]:
df_words['dossier'] = df_words['text_id'].apply(pnum_to_dossier)

In [102]:
df_dossier_a = df[df['dossier'].str.contains('.a')]
df_dossier_a

a            b    break                cf     epos  f          file  \
0                    a  damaged             awātu        N     P224485.json   
1                  bat                      awātu        N     P224485.json   
2                LUGAL                      šarru        N     P224485.json   
3                    a                        ana      PRP     P224485.json   
4                   na                        ana      PRP  t  P224485.json   
5               1(diš)           Aššur-šarru-uṣur       PN     P224485.json   
6                   aš           Aššur-šarru-uṣur       PN     P224485.json   
7                  šur           Aššur-šarru-uṣur       PN     P224485.json   
8                  MAN           Aššur-šarru-uṣur       PN     P224485.json   
9                  PAB  damaged  Aššur-šarru-uṣur       PN     P224485.json   
10                 šul  damaged             šulmu        N     P224485.json   
11                  mu                      šulmu        N     P224485.json   
12                  ia                      yâšim       IP     P224485.json   
13                   a  damaged             yâšim       IP     P224485.json   
14                  ši                      yâšim       IP     P224485.json   
15                 šul  damaged             šulmu        N     P224485.json   
16                  mu                      šulmu        N     P224485.json   
17                   a                        ana      PRP     P224485.json   
18                  na                        ana      PRP  t  P224485.json   
19                 KUR                  Mat-Aššur       GN     P224485.json   
20                  aš                  Mat-Aššur       GN     P224485.json   
21                 šur                  Mat-Aššur       GN     P224485.json   
22                  KI                  Mat-Aššur       GN     P224485.json   
23                 ŠA₃  damaged             libbu        N     P224485.json   
24                  ka  missing             libbu        N     P224485.json   
25                  lu  damaged                lū      MOD     P224485.json   
26                DUG₃                       ṭābu       AJ     P224485.json   
27                  GA                       ṭābu       AJ     P224485.json   
28                  ka                       ṭābu       AJ     P224485.json   
29                  ša  damaged                ša      REL     P224485.json   
30                 taš                     šapāru        V     P224485.json   
31                 pur                     šapāru        V     P224485.json   
32                  an                     šapāru        V     P224485.json   
33                  ni                     šapāru        V     P224485.json   
34                  ma                         mā      PRP     P224485.json   
35                   a                         mā      PRP     P224485.json   
36      v          LU₂                       māru        N     P224485.json   
37                   A                       māru        N     P224485.json   
38                 šip                       māru        N     P224485.json   
39                  ri  damaged              māru        N     P224485.json   
40                  ša  missing                ša      DET     P224485.json   
41              1(diš)                       Mita       PN     P224485.json   
42                  me                       Mita       PN     P224485.json   
43                  ta                       Mita       PN     P224485.json   
44                   a                       Mita       PN     P224485.json   
45                 KUR                    Muskaya       EN     P224485.json   
46                 mus                    Muskaya       EN     P224485.json   
47                  ka                    Muskaya       EN     P224485.json   
48                   a                    Muskaya       EN     P224485.json   
49                   a                    Muskaya       EN

In [400]:
df_words_dossier_a = df_words[df_words['dossier'].str.contains('.a')]
df_words_dossier_a

cf epos          file                   form  \
0                 awātu    N  P224485.json                  a-bat   
1                 šarru    N  P224485.json                  LUGAL   
2                   ana  PRP  P224485.json                   a-na   
3      Aššur-šarru-uṣur   PN  P224485.json      {1}aš-šur-MAN-PAB   
4                 šulmu    N  P224485.json                 šul-mu   
5                 yâšim   IP  P224485.json                ia-a-ši   
6                 šulmu    N  P224485.json                 šul-mu   
7                   ana  PRP  P224485.json                   a-na   
8             Mat-Aššur   GN  P224485.json         KUR-aš-šur{KI}   
9                 libbu    N  P224485.json                 ŠA₃-ka   
10                   lū  MOD  P224485.json                     lu   
11                 ṭābu   AJ  P224485.json             DUG₃.GA-ka   
12                   ša  REL  P224485.json                     ša   
13               šapāru    V  P224485.json          taš-pur-an-ni   
14                   mā  PRP  P224485.json                   ma-a   
15                 māru    N  P224485.json          {LU₂}A-šip-ri   
16                   ša  DET  P224485.json                     ša   
17                 Mita   PN  P224485.json             {1}me-ta-a   
18              Muskaya   EN  P224485.json        {KUR}mus-ka-a.a   
19                  ina  PRP  P224485.json                    ina   
20                muhhu    N  P224485.json              UGU-hi-ia   
21                alāku    V  P224485.json              it-tal-ka   
22                   mā  PRP  P224485.json                   ma-a   
24                 ṣābu    N  P224485.json               ERIM-MEŠ   
25               Quwaya   EN  P224485.json          {KUR}qu-u-a.a   
26                   ša  REL  P224485.json                     ša   
27                 Urik   PN  P224485.json            {1}u₂-ri-ik   
28                  ana  PRP  P224485.json                   a-na   
29                šapru    N  P224485.json         {LU₂}šap-ru-te   
30                  ana  PRP  P224485.json                   a-na   
31               Urarṭu   GN  P224485.json               {KUR}URI   
32               wabālu    V  P224485.json       u₂-še-bi-lu-u-ni   
33                   mā  PRP  P224485.json                   ma-a   
34                  ina  PRP  P224485.json                    ina   
35                muhhu    N  P224485.json              UGU-hi-ia   
36                 našû   AJ  P224485.json                  na-ṣa   
37                tarṣu   AJ  P224485.json               ta-ri-iṣ   
38              adanniš   AV  P224485.json              a-dan-niš   
39               annûri   AV  P224485.json              an-nu-rig   
40                Aššur   DN  P224485.json                 aš-šur   
41                Šamaš   DN  P224485.json             {d}ša₂-maš   
42                  Bel   DN  P224485.json                     EN   
43                 Nabu   DN  P224485.json                  {d}AG   
44                  ilu    N  P224485.json          DINGIR-MEŠ-ia   
45                epēšu    V  P224485.json              e-tap-šu₂   
46                   lā  MOD  P224485.json                     la   
47                  ina  PRP  P224485.json                    ina   
48                libbu    N  P224485.json                    ŠA₃   
49               qarābu    N  P224485.json               qa-ra-bi   
50                   lā  MOD  P224485.json                     la   
51                  ina  PRP  P224485.json                    ina   
52                libbu    N  P224485.json                    ŠA₃   
53               memēni   XP  P224485.json               me-me-ni   
54              Muskaya   EN  P224485.json        {KUR}mus-ka-a.a   
55                   pû    N  P224485.json               pi-i-šu₂   
56               tadānu    V  P224485.json      it-ta-an-na-na-ši   
57                  ana  PRP  P224485.json                   a-na   
58                s

In [147]:
#pnum_list_a = list(df_dossier_a[df_dossier_a['dossier'].isin(['SAA01.03.01.a','SAA01.04.01.a'])]['text_id'].unique())
pnum_list_a = list(df_dossier_a['text_id'].unique())
pnum_list_a

['P224485',
 'P237089',
 'P313419',
 'P313420',
 'P313421',
 'P313434',
 'P313435',
 'P313437',
 'P313439',
 'P313447',
 'P313448',
 'P313472',
 'P313478',
 'P313479',
 'P313504',
 'P313510',
 'P313515',
 'P313523',
 'P313540',
 'P313542',
 'P313551',
 'P313626',
 'P313630',
 'P313640',
 'P313750',
 'P313788',
 'P313874',
 'P313911',
 'P313926',
 'P314044',
 'P334020',
 'P334036',
 'P334037',
 'P334038',
 'P334039',
 'P334040',
 'P334041',
 'P334042',
 'P334043',
 'P334044',
 'P334045',
 'P334046',
 'P334047',
 'P334048',
 'P334049',
 'P334050',
 'P334051',
 'P334053',
 'P334054',
 'P334055',
 'P334060',
 'P334069',
 'P334070',
 'P334071',
 'P334072',
 'P334073',
 'P334074',
 'P334075',
 'P334076',
 'P334077',
 'P334078',
 'P334079',
 'P334080',
 'P334081',
 'P334083',
 'P334084',
 'P334090',
 'P334091',
 'P334092',
 'P334094',
 'P334097',
 'P334099',
 'P334100',
 'P334101',
 'P334102',
 'P334103',
 'P334104',
 'P334105',
 'P334106',
 'P334108',
 'P334109',
 'P334111',
 'P334113',
 'P3

In [190]:
df_opening_counts = pd.read_csv('opening_counts.csv',encoding='utf-8')
df_opening_counts = df_opening_counts.fillna(0)
df_opening_counts = df_opening_counts.drop_duplicates()
df_opening_counts = df_opening_counts.set_index('id_text')
df_opening_counts

nos_words
id_text           
P334656        0.0
P334282        0.0
P334723        0.0
P334210        0.0
P334357        0.0
P334209        0.0
X900010        0.0
P334222        0.0
P334361        0.0
X900005        0.0
X900007        0.0
P334165        0.0
P334789        0.0
P313542        0.0
P334347       19.0
P334351       19.0
P334350       19.0
P334348       19.0
P334349       19.0
P334296       19.0
P334559       10.0
P334558       10.0
P334555       10.0
P334151        0.0
P334180        0.0
P334181        0.0
P334182        0.0
P313479        0.0
P313478        0.0
P334179        0.0
P334177        0.0
P334178        0.0
P334529       10.0
P334528       10.0
P334187       10.0
P313448       10.0
P334186       10.0
P334625        0.0
P334258        0.0
P334339       10.0
P337150       10.0
P334338       10.0
P334091        9.0
P334256       10.0
P334094       10.0
P334090       10.0
P334092       23.0
P334257       10.0
P313523        0.0
P313439        0.0
...            ...
P334042       16.0
P334043       16.0
P334044       16.0
P334045       16.0
P334047       16.0
P334271       16.0
P334273       16.0
P334328       16.0
P334330       16.0
P334331       16.0
P336167       16.0
P334332       11.0
P334903        0.0
P334658        0.0
P334588        0.0
P334281        0.0
P334060        0.0
P334543        0.0
P334280        0.0
P334223        0.0
P334102        0.0
P334499        0.0
P334100        0.0
P334101        0.0
P313419       20.0
P313551        0.0
P313626        0.0
P313874        9.0
P334046       10.0
P334083       10.0
P334113       10.0
P334124       10.0
P334135       10.0
P334136       10.0
P334158       22.0
P334170       10.0
P334171       22.0
P334172       22.0
P334174       10.0
P334175       10.0
P334176       10.0
P334212        5.0
P334259        5.0
P334288       10.0
P334329       17.0
P334554       10.0
P334587       23.0
P334665       16.0
P336168       10.0
0              0.0

[276 rows x 1 columns]

In [191]:
df_opening_a = pd.DataFrame()
for pnum in pnum_list_a:
    try:
        #print('Good: '+pnum)
        df_pnum = df_dossier_a[(df_dossier_a['text_id'] == pnum) & (df_dossier_a['word_num'] <= df_opening_counts.loc[pnum]['nos_words'])]
        df_opening_a = pd.concat([df_opening_a,df_pnum])
    except KeyError:
        #print(pnum)
        continue
df_opening_a.to_csv('output/opening_signs_sargon.csv',encoding='utf-8')

In [275]:
df_opening_a

a             b    break                cf     epos  f          file  \
1123                 a                        ana      PRP     P237089.json   
1124                na                        ana      PRP     P237089.json   
1125             LUGAL                      šarru        N     P237089.json   
1126                be                       bēlu        N     P237089.json   
1127               li₂                       bēlu        N     P237089.json   
1128               ia₂                       bēlu        N     P237089.json   
1129              ARAD                       ardu        N     P237089.json   
1130                ka                       ardu        N     P237089.json   
1131            1(diš)                 Issar-duri       PN     P237089.json   
1132                 d                 Issar-duri       PN     P237089.json   
1133       1(u) 5(diš)  damaged        Issar-duri       PN     P237089.json   
1134                du                 Issar-duri       PN     P237089.json   
1135                ri                 Issar-duri       PN     P237089.json   
1136                lu  damaged                lū      MOD     P237089.json   
1137                 u                         lū      MOD     P237089.json   
1138                DI                      šulmu        N     P237089.json   
1139                mu                      šulmu        N     P237089.json   
1140                 a                        ana      PRP     P237089.json   
1141                na                        ana      PRP     P237089.json   
1142             LUGAL  damaged             šarru        N     P237089.json   
1143                EN                       bēlu        N     P237089.json   
1144               ia₂                       bēlu        N     P237089.json   
2029                 a  missing               ana      PRP     P313419.json   
2030                na  missing               ana      PRP     P313419.json   
2031             LUGAL  missing             šarru        N     P313419.json   
2032                EN  missing              bēlu        N     P313419.json   
2033                ia                       bēlu        N     P313419.json   
2034              ARAD  missing              ardu        N     P313419.json   
2035                ka  missing              ardu        N     P313419.json   
2036            1(diš)  missing             no-cf  no-epos     P313419.json   
2037                 d  missing             no-cf  no-epos     P313419.json   
2038                 x  missing             no-cf  no-epos     P313419.json   
2039                                        no-cf  no-epos     P313419.json   
2040               GIN                      no-cf  no-epos     P313419.json   
2041                in                      no-cf  no-epos     P313419.json   
2042                lu  missing                lū      MOD     P313419.json   
2043                DI  missing             šulmu        N     P313419.json   
2044                mu  missing             šulmu        N     P313419.json   
2045                 a  missing               ana      PRP     P313419.json   
2046                na  missing               ana      PRP     P313419.json   
2047             LUGAL  missing             šarru        N     P313419.json   
2048                EN  damaged              bēlu        N     P313419.json   
2049                ia  damaged              bēlu        N     P313419.json   
2050                DI  missing             šulmu        N     P313419.json   
2051                mu  missing             šulmu        N     P313419.json   
2052                 a  missing               ana      PRP     P313419.json   
2053                na  missing               ana      PRP     P313419.json   
2054               URU  missing             birtu        N     P313419.json   
2055                bi  missing             birtu        N     P313419.json   
2056                ra  missing             birtu        

In [223]:
len(list(df_opening_a['text_id'].unique()))

164

In [216]:
df_opening_a_2 = df_opening_a[df_opening_a['dossier'].isin(['SAA01.03.01.a','SAA01.04.01.a'])]

In [221]:
df_dist_paleo = pd.DataFrame(df_opening_a.groupby(['sign_form','combined']).apply(lambda row: ','.join(row['sign_loc_id'] + ' (' + row['line_label'] + ')'))).reset_index() #.to_csv('output/dist_ortho_sign_opening.csv',encoding='utf-8')

df_dist_paleo.columns = ['sign_form','combined','all_locs']
df_dist_paleo['count'] = df_dist_paleo['all_locs'].apply(lambda x: len(x.split(',')))
df_dist_paleo['is_dup'] = df_dist_paleo.duplicated(['sign_form'],False)
df_dist_paleo = df_dist_paleo[df_dist_paleo['is_dup'] == True]
df_dist_paleo.to_csv('output/dist_paleo_opening.csv',encoding='utf-8')
df_dist_paleo

sign_form        combined  \
3            AK           AK:..   
4            AK          AK:.d.   
5            AK         AK:.td.   
9          ARAD         ARAD:..   
10         ARAD        ARAD:.p.   
17           BU           BU:..   
18           BU          BU:.t.   
19           BU        BU:.tdp.   
20           BU         BU:.tp.   
21           DA           DA:..   
22           DA          DA:.d.   
23           DI           DI:..   
24           DI          DI:.d.   
27           DU           DU:..   
28           DU          DU:.d.   
33           E₂           E₂:..   
34           E₂          E₂:.d.   
50           KA           KA:..   
51           KA          KA:.d.   
58           LU           LU:..   
59           LU          LU:.m.   
60        LUGAL        LUGAL:..   
61        LUGAL       LUGAL:.d.   
62        LUGAL       LUGAL:.m.   
63        LUGAL       LUGAL:.p.   
64        LUGAL       LUGAL:.t.   
65        LUGAL      LUGAL:.tm.   
66        LUGAL       LUGAL:.y.   
67          LUH          LUH:..   
68          LUH         LUH:.p.   
69          LU₂          LU₂:..   
70          LU₂         LU₂:v..   
71          LU₂        LU₂:v.y.   
76           MU           MU:..   
77           MU          MU:.d.   
78           MU          MU:.p.   
79           MU         MU:.pp.   
80           MU          MU:.t.   
82           NA           NA:..   
83           NA          NA:.d.   
84           NA          NA:.t.   
85           NA         NA:.td.   
86           NA          NA:.y.   
87           NI           NI:..   
88           NI          NI:.d.   
89           NI          NI:.t.   
91          NUN          NUN:..   
92          NUN         NUN:.m.   
97           RA           RA:..   
98           RA          RA:.t.   
99           RA        RA:.tdp.   
100          RI           RI:..   
101          RI          RI:.d.   
102          RU           RU:..   
103          RU         RU:.dp.   
110          TI           TI:..   
111          TI          TI:.t.   
117         URU          URU:..   
118         URU         URU:.d.   
119          U₂           U₂:..   
120          U₂          U₂:.m.   
127  |EZEN×BAD|   |EZEN×BAD|:..   
128  |EZEN×BAD|  |EZEN×BAD|:.p.   
134  |ME.U.U.U|   |ME.U.U.U|:..   
135  |ME.U.U.U|  |ME.U.U.U|:.m.   
136  |ME.U.U.U|  |ME.U.U.U|:.t.   
145          ŠA           ŠA:..   
146          ŠA          ŠA:.d.   
147          ŠA         ŠA:.dm.   
148          ŠA         ŠA:.dt.   
149          ŠA        ŠA:.dtm.   
150          ŠA         ŠA:.dy.   
151          ŠA          ŠA:.m.   
152          ŠA          ŠA:.p.   
153          ŠA         ŠA:.tp.   
154          ŠA          ŠA:.y.   
155          ŠA        ŠA:.ydm.   
157         ŠA₃          ŠA₃:..   
158         ŠA₃         ŠA₃:.p.   

                                              all_locs  count  is_dup  
3    P334078.3.2.2 (o 2),P334078.5.1.1 (o 4),P33407...     12    True  
4                                  P313435.3.2.2 (o 2)      1    True  
5                                  P334665.3.2.5 (o 2)      1    True  
9    P237089.3.1.0 (o 2),P313419.3.1.0 (o 2),P31342...    162    True  
10   P313421.3.1.0 (o 2),P313504.3.1.0 (o 2),P31364...      3    True  
17   P313435.6.4.2 (o 5),P313472.3.2.6 (o 2),P31351...     28    True  
18   P313420.7.4.1 (o 6),P334271.6.2.2 (o 5),P33433...      4    True  
19                                 P334665.8.1.2 (o 7)      1    True  
20                                 P334037.6.1.2 (o 5)      1    True  
21             P313420.3.2.3 (o 2),P334343.3.2.3 (o 2)      2    True  
22   P334344.3.2.3 (o 2),P334345.3.2.3 (o 2),P33434...      3    True  
23   P237089.4.2.0 (o 3),P313419.4.2.0 (o 3),P31341...    184    True  
24   P313437.4.2.0 (o 3),P313447.4.2.0 (o 3),P33404...     21    True  
27   P237089.3.2.3 (o 2),P313419.3.2.5 (o 2),P31343...     17    True  
28   P334114.3.2.4 (o 2),P334116.3.2.4 (o 2),P33450...      5    True  
33   P334036.3.2.4 (o 2),P334038.3.2.4 (o 2),P33403..

In [333]:
sign_list = ['AG','ARAD','DI','E₂','LU₂','|ME.U.U.U|','MU','NI','NUN','RU','ŠA','ŠA₃','TI','U₂','URU','KA','LU']
df_special_signs_open = pd.DataFrame(df_opening_a[(df_opening_a['sign_form'].isin(sign_list)) &
                                                 (df_opening_a['mods_str'] != '..')].groupby('text_id').agg('count')['a'])
df_special_sort = df_special_signs_open.sort_values(by='a',ascending=False).head(5)
df_special_sort

a
text_id   
P334080  5
P334534  5
P334505  4
P334091  4
P334092  4

Compare Openings to Rest of Text

In [315]:
list_pnums_open = list(df_opening_a['text_id'].unique())
sign_loc_list = list(df_opening_a['sign_loc_id'])
df_nonopen_a = df_dossier_a[~(df_dossier_a['sign_loc_id'].isin(sign_loc_list)) & (df_dossier_a['text_id'].isin(list_pnums_open))]
df_nonopen_a

a       b    break                cf     epos  f          file  \
1145           ša  missing                ša      REL     P237089.json   
1146        LUGAL                      šarru        N     P237089.json   
1147           be                       bēlu        N     P237089.json   
1148          li₂  damaged              bēlu        N     P237089.json   
1149           iš  missing            šapāru        V     P237089.json   
1150          pur  damaged            šapāru        V     P237089.json   
1151           an                     šapāru        V     P237089.json   
1152           ni                     šapāru        V     P237089.json   
1153           ma  missing                mā      PRP     P237089.json   
1154            a  missing                mā      PRP     P237089.json   
1155            x  missing             no-cf  no-epos     P237089.json   
1156            x  missing             no-cf  no-epos     P237089.json   
1157    v     LU₂  damaged           Ituʾaya       EN     P237089.json   
1158            i                    Ituʾaya       EN     P237089.json   
1159          tu₂  missing           Ituʾaya       EN     P237089.json   
1160            a  missing           Ituʾaya       EN     P237089.json   
1161            a  missing           Ituʾaya       EN     P237089.json   
1162           ša                         ša      REL     P237089.json   
1163         dul₆                      dullu        N     P237089.json   
1164           lu                      dullu        N     P237089.json   
1165          ina  missing               ina      PRP     P237089.json   
1166          URU  missing      Dur-Šarruken       GN     P237089.json   
1167         BAD₃  missing      Dur-Šarruken       GN     P237089.json   
1168          MAN  missing      Dur-Šarruken       GN     P237089.json   
1169          GIN  damaged      Dur-Šarruken       GN     P237089.json   
1170           ep  missing             epēšu        V     P237089.json   
1171           pu  damaged             epēšu        V     P237089.json   
1172           šu                      epēšu        V     P237089.json   
1173            u                      epēšu        V     P237089.json   
1174           ni                      epēšu        V     P237089.json   
1175            x  missing             no-cf  no-epos     P237089.json   
1176            x  missing             no-cf  no-epos     P237089.json   
1177            x  missing             no-cf  no-epos     P237089.json   
1178            x  missing             no-cf  no-epos     P237089.json   
1179            x  missing             no-cf  no-epos     P237089.json   
1180            x  missing             no-cf  no-epos     P237089.json   
1181           ma                      no-cf  no-epos     P237089.json   
1182           ri                      no-cf  no-epos     P237089.json   
1183            o  missing             no-cf  no-epos     P237089.json   
1184            x  missing             no-cf  no-epos     P237089.json   
1185            x  missing             no-cf  no-epos     P237089.json   
1186            x  missing             no-cf  no-epos     P237089.json   
1187            x  missing             no-cf  no-epos     P237089.json   
1188            x  missing             no-cf  no-epos     P237089.json   
1190           ni  damaged             no-cf  no-epos     P237089.json   
1191            x  damaged             no-cf  no-epos     P237089.json   
1192           li                     sahāru        V     P237089.json   
1193           is                     sahāru        V     P237089.json   
1194           hu                     sahāru        V     P237089.json   
1195           ra                     sahāru        V     P237089.json   
1196           ma                   maṣṣartu        N     P237089.json   
1197          ṣar                   maṣṣartu        N     P237089.json   
1198           ti                   maṣṣartu        N  t  P237089.json   
1199        

In [372]:
df_open_std = df_opening_a[(df_opening_a['sign_form'].isin(sign_list)) & (df_opening_a['mods_str'] == '..')]
df_open_nstd = df_opening_a[(df_opening_a['sign_form'].isin(sign_list)) & (df_opening_a['mods_str'] != '..')]

df_nonopen_std = df_nonopen_a[(df_nonopen_a['sign_form'].isin(sign_list)) & (df_nonopen_a['mods_str'] == '..')]
df_nonopen_nstd = df_nonopen_a[(df_nonopen_a['sign_form'].isin(sign_list)) & (df_nonopen_a['mods_str'] != '..')]

In [381]:
df_open_std_counts = pd.DataFrame(df_open_std.groupby(['text_id','sign_form']).agg('count')['a'])
df_open_nstd_counts = pd.DataFrame(df_open_nstd.groupby(['text_id','sign_form']).agg('count')['m'])
df_nonopen_std_counts = pd.DataFrame(df_nonopen_std.groupby(['text_id','sign_form']).agg('count')['f'])
df_nonopen_nstd_counts = pd.DataFrame(df_nonopen_nstd.groupby(['text_id','sign_form']).agg('count')['b'])

df_open_counts_all = pd.concat([df_open_std_counts,df_open_nstd_counts,df_nonopen_std_counts,df_nonopen_nstd_counts],axis=1)
df_open_counts_all = df_open_counts_all.fillna(0).reset_index()
df_open_counts_all

text_id   sign_form    a    m     f    b
0     P237089        ARAD  1.0  0.0   0.0  0.0
1     P237089          DI  1.0  0.0   0.0  0.0
2     P237089          KA  1.0  0.0   0.0  0.0
3     P237089          LU  1.0  0.0   2.0  0.0
4     P237089         LU₂  0.0  0.0   0.0  1.0
5     P237089          MU  1.0  0.0   0.0  0.0
6     P237089          NI  1.0  0.0   4.0  0.0
7     P237089          TI  0.0  0.0   0.0  1.0
8     P237089         URU  0.0  0.0   1.0  0.0
9     P237089          ŠA  0.0  0.0   2.0  1.0
10    P237089         ŠA₃  0.0  0.0   1.0  0.0
11    P313419        ARAD  1.0  0.0   0.0  0.0
12    P313419          DI  2.0  0.0   1.0  0.0
13    P313419          KA  1.0  0.0   1.0  0.0
14    P313419          LU  1.0  0.0   1.0  0.0
15    P313419         LU₂  0.0  0.0   0.0  1.0
16    P313419          MU  2.0  0.0   1.0  0.0
17    P313419          NI  0.0  0.0   4.0  1.0
18    P313419         NUN  0.0  0.0   1.0  0.0
19    P313419          RU  0.0  0.0   2.0  0.0
20    P313419          TI  1.0  0.0   0.0  0.0
21    P313419         URU  1.0  0.0   0.0  0.0
22    P313419          U₂  0.0  0.0   2.0  0.0
23    P313419          ŠA  1.0  0.0   1.0  1.0
24    P313420        ARAD  1.0  0.0   0.0  0.0
25    P313420          DI  2.0  0.0   1.0  0.0
26    P313420          KA  1.0  0.0   2.0  0.0
27    P313420          LU  2.0  0.0   0.0  0.0
28    P313420          MU  2.0  0.0   1.0  0.0
29    P313420          NI  4.0  0.0   8.0  0.0
30    P313420         NUN  0.0  0.0   0.0  1.0
31    P313420          RU  0.0  0.0   1.0  0.0
32    P313420          TI  0.0  1.0   2.0  1.0
33    P313420         URU  1.0  0.0   2.0  0.0
34    P313420  |ME.U.U.U|  0.0  0.0   0.0  4.0
35    P313420          ŠA  2.0  0.0   4.0  4.0
36    P313420         ŠA₃  1.0  0.0   2.0  0.0
37    P313421        ARAD  0.0  1.0   0.0  1.0
38    P313421          DI  1.0  0.0   0.0  0.0
39    P313421          KA  1.0  0.0   0.0  0.0
40    P313421          LU  1.0  0.0   0.0  0.0
41    P313421         LU₂  0.0  0.0   0.0  1.0
42    P313421          MU  1.0  0.0   0.0  0.0
43    P313421          NI  2.0  0.0   2.0  0.0
44    P313421          U₂  0.0  0.0   1.0  1.0
45    P313421  |ME.U.U.U|  0.0  0.0   0.0  1.0
46    P313421          ŠA  0.0  0.0   0.0  3.0
47    P313421         ŠA₃  0.0  0.0   1.0  0.0
48    P313434        ARAD  1.0  0.0   0.0  0.0
49    P313434          DI  1.0  0.0   0.0  1.0
50    P313434          KA  1.0  0.0   2.0  0.0
51    P313434          LU  1.0  0.0   0.0  0.0
52    P313434         LU₂  0.0  0.0   0.0  7.0
53    P313434          MU  1.0  0.0   1.0  0.0
54    P313434          NI  1.0  0.0   2.0  0.0
55    P313434         NUN  0.0  0.0   0.0  1.0
56    P313434         URU  0.0  0.0   1.0  0.0
57    P313434          U₂  0.0  0.0   0.0  4.0
58    P313434  |ME.U.U.U|  0.0  0.0   7.0  1.0
59    P313434          ŠA  0.0  0.0   3.0  1.0
60    P313435        ARAD  1.0  0.0   0.0  0.0
61    P313435          DI  1.0  0.0   1.0  0.0
62    P313435          KA  1.0  0.0   0.0  0.0
63    P313435          LU  1.0  0.0   0.0  0.0
64    P313435         LU₂  0.0  0.0   1.0  0.0
65    P313435          MU  1.0  0.0   0.0  0.0
66    P313435          NI  0.0  0.0   7.0  0.0
67    P313435          RU  1.0  0.0   0.0  0.0
68    P313435          TI  0.0  0.0   1.0  0.0
69    P313435         URU  0.0  0.0   2.0  0.0
70    P313435          U₂  0.0  0.0   3.0  0.0
71    P313435  |ME.U.U.U|  0.0  0.0   3.0  1.0
72    P313435          ŠA  0.0  0.0   3.0  0.0
73    P313435         ŠA₃  0.0  0.0   2.0  0.0
74    P313437        ARAD  1.0  0.0   0.0  0.0
75    P313437          DI  0.0  1.0   0.0  0.0
76    P313437          KA  1.0  0.0   1.0  0.0
77    P313437          LU  1.0  0.0   0.0  0.0
78    P313437          MU  1.0  0.0   0.0  0.0
79    P313437          NI  0.0  0.0   6.0  0.0
80    P313437          TI  0.0  0.0   2.0  0.0
81    P313437         URU  0.0  0.0   1.0  0.0
82    P313437  |ME.U.U.U|  0.0  0.0   3.0  1.0
83    P313437          ŠA  0.0  0.0   1.0  2.0
84    P3134

In [384]:
d = {'n0':0,'n1':0,'n2':0,'n3':0}
for i, row in df_open_counts_all.iterrows():
    if row['a'] > 0.0 and row['m'] > 0.0:
        d['n3'] += 1
    elif row['a'] == 0.0 and row['m'] == 0.0:
        d['n0'] += 1
    elif row['f'] == 0.0 and row['b'] == 0.0:
        d['n0'] += 1
    elif row['a'] > 0 and row['m'] == 0.0 and row['f'] > 0 and row['b'] == 0.0:
        d['n1'] += 1
    elif row['a'] == 0.0 and row['m'] > 0.0 and row['f'] == 0.0 and row['b'] > 0.0:
        d['n1'] += 1
    else:
        d['n2'] += 1
d

{'n0': 1412, 'n1': 454, 'n2': 75, 'n3': 14}

In [390]:
print('Percent of signs forms consistently represented between opening formula and rest of letter:')
print("{0:.2%}".format(d['n1'] / (d['n1'] + d['n2'])))
print('Percent of sign forms INconsistently represented between opening formula and rest of letter:')
print("{0:.2%}".format(d['n2'] / (d['n1'] + d['n2'])))
print('Percent of sign forms INconsistently represented in opening formula itself:')
print("{0:.2%}".format(d['n3'] / (d['n1'] + d['n2'] + d['n3'])))

Percent of signs forms consistently represented between opening formula and rest of letter:
85.82%
Percent of sign forms INconsistently represented between opening formula and rest of letter:
14.18%
Percent of sign forms INconsistently represented in opening formula itself:
2.58%


Same for word usage

In [403]:
df_words_opening_a = pd.DataFrame()
df_words_nonopen_a = pd.DataFrame()
for pnum in pnum_list_a:
    try:
        #print('Good: '+pnum)
        df_pnum = df_words_dossier_a[(df_words_dossier_a['text_id'] == pnum) & (df_words_dossier_a['word_num'] <= df_opening_counts.loc[pnum]['nos_words'])]
        df_words_opening_a = pd.concat([df_words_opening_a,df_pnum])
        
        df_pnum = df_words_dossier_a[(df_words_dossier_a['text_id'] == pnum) & (df_words_dossier_a['word_num'] > df_opening_counts.loc[pnum]['nos_words'])]
        df_words_nonopen_a = pd.concat([df_words_nonopen_a,df_pnum])
    except KeyError:
        #print(pnum)
        continue
#df_words_opening_a
df_words_nonopen_a = df_words_nonopen_a[df_words_nonopen_a['text_id'].isin(list(df_words_opening_a['text_id'].unique()))]
df_words_nonopen_a

cf epos          file                     form  \
443                  ša  REL  P237089.json                       ša   
444               šarru    N  P237089.json                    LUGAL   
445                bēlu    N  P237089.json                   be-li₂   
446              šapāru    V  P237089.json             iš-pur-an-ni   
447                  mā  PRP  P237089.json                     ma-a   
450             Ituʾaya   EN  P237089.json           {LU₂}i-tu₂-a.a   
451                  ša  REL  P237089.json                       ša   
452               dullu    N  P237089.json                  dul₆-lu   
453                 ina  PRP  P237089.json                      ina   
454        Dur-Šarruken   GN  P237089.json        {URU}BAD₃-MAN-GIN   
455               epēšu    V  P237089.json            ep-pu-šu-u-ni   
470              sahāru    V  P237089.json              li-is-hu-ra   
471            maṣṣartu    N  P237089.json                ma-ṣar-ti   
472               dannu   AJ  P237089.json                dan-na-at   
473               libbu    N  P237089.json                      ŠA₃   
474                  ša  DET  P237089.json                       ša   
475               šarru    N  P237089.json                    LUGAL   
476                bēlu    N  P237089.json                   EN-ia₂   
477                  lū  MOD  P237089.json                       lu   
478                ṭābu   AJ  P237089.json                  DUG₃.GA   
979               šarru    N  P313419.json                    LUGAL   
996                  lā  MOD  P313419.json                       la   
997                wadû    V  P313419.json                 nu-u₂-da   
998                  ša  REL  P313419.json                       ša   
1007               qabû    V  P313419.json           iq-ṭi₂-bu-u-ni   
1008                 mā  PRP  P313419.json                     ma-a   
1009             namāšu    V  P313419.json              ut-ta-mi-iš   
1016                 mā  PRP  P313419.json                     ma-a   
1017                 lā  MOD  P313419.json                       la   
1018             namāšu    V  P313419.json             u₂-nam-mi-iš   
1026                 mā  PRP  P313419.json                     ma-a   
1027                ina  PRP  P313419.json                      ina   
1050                 mā  PRP  P313419.json                     ma-a   
1069                 mā  PRP  P313419.json                     ma-a   
1070           maṣṣartu    N  P313419.json            EN.NUN-šu₂-nu   
1071             naṣāru    V  P313419.json               i-na-ṣu-ru   
1072             šapāru    V  P313419.json                 a-sa-par   
1073              alāku    V  P313419.json                it-tal-ku   
1074               šâlu    V  P313419.json            i-ša₂-ʾu-u-lu   
1075               ṭēmu    N  P313419.json                 ṭe₃-e-mu   
1076              harṣu   AJ  P313419.json                   har-ṣu   
1077              alāku    V  P313419.json            il-la-ku-u-ni   
1078               qabû    V  P313419.json            i-qab-bu-u-ni   
1079                ana  PRP  P313419.json                     a-na   
1080              šarru    N  P313419.json                    LUGAL   
1081               bēlu    N  P313419.json                    EN-ia   
1082             šapāru    V  P313419.json              a-šap-pa-ra   
1083             annûri   AV  P313419.json                an-nu-rig   
1084               ṣīru    N  P313419.json                 {LU₂}MAH   
1085           Šubriaya   EN  P313419.json          {KUR}šub-ri-a.a   
1086                ina  PRP  P313419.json                      ina   
1087               pānu    N  P313419.json                      IGI   
1088              šarru    N  P313419.json                    LUGAL   
1089               bēlu    N  P313419.json                    EN-ia   
1090              alāku    V  P313419.json                 il-la-ka   
1091               mīnu   QP  P313419.json   

In [428]:
word_list = ['šulmu[completeness]N:šulmu','bēlu[lord]N:bēlīya','bēlu[lord]N:bēlī','lū[may]MOD:lū','šarru[king]N:šarru','šarru[king]N:šarri']

In [429]:
df_words_open_std = df_words_opening_a[(df_words_opening_a['lemma_norm'].isin(word_list))]
#df_open_nstd = df_words_opening_a[(df_words_opening_a['lemma_norm'].isin(sign_list)) & (df_words_opening_a['mods_str'] != '..')]

df_words_nonopen_std = df_words_nonopen_a[(df_words_nonopen_a['lemma_norm'].isin(word_list))]
#df_nonopen_nstd = df_words_nonopen_a[(df_words_nonopen_a['lemma_norm'].isin(sign_list)) & (df_words_nonopen_a['mods_str'] != '..')]

#df_words_open_std

In [430]:
df_words_open_std_counts = pd.DataFrame(df_words_open_std.groupby(['text_id','lemma_norm','lemma_norm_form']).agg('count')['cf'])
df_words_nonopen_std_counts = pd.DataFrame(df_words_nonopen_std.groupby(['text_id','lemma_norm','lemma_norm_form']).agg('count')['gw'])
#df_words_open_std_counts

In [431]:
df_words_opening_counts_all = pd.concat([df_words_open_std_counts,df_words_nonopen_std_counts],axis=1)
df_words_opening_counts_all.fillna(0).to_csv('test.csv',encoding='utf-16',sep='\t')

PermissionError: [Errno 13] Permission denied: 'test.csv'

In [432]:
df_words_opening_notext = pd.DataFrame(df_words_open_std.groupby(['lemma_norm','lemma_norm_form']).agg('count')['cf'])
df_words_nonopen_notext = pd.DataFrame(df_words_nonopen_std.groupby(['lemma_norm','lemma_norm_form']).agg('count')['gw'])
df_words_opening_notext_all = pd.concat([df_words_opening_notext,df_words_nonopen_notext],axis=1)
df_words_opening_notext_all

cf   gw
lemma_norm                 lemma_norm_form                              
bēlu[lord]N:bēlī           bēlu[lord]N:bēlī:BE-i                NaN    1
                           bēlu[lord]N:bēlī:EN                  NaN   53
                           bēlu[lord]N:bēlī:be-li               NaN    7
                           bēlu[lord]N:bēlī:be-li₂              NaN  158
                           bēlu[lord]N:bēlī:be-li₂-i            NaN    1
bēlu[lord]N:bēlīya         bēlu[lord]N:bēlīya:BE-ia             4.0    2
                           bēlu[lord]N:bēlīya:BE-ia₂            NaN    1
                           bēlu[lord]N:bēlīya:EN-a             18.0    7
                           bēlu[lord]N:bēlīya:EN-ia           172.0   50
                           bēlu[lord]N:bēlīya:EN-ia₂           56.0   32
                           bēlu[lord]N:bēlīya:be-li₂-a          2.0    2
                           bēlu[lord]N:bēlīya:be-li₂-ia        77.0   21
                           bēlu[lord]N:bēlīya:be-li₂-ia₂       47.0   18
lū[may]MOD:lū              lū[may]MOD:lū:lu                   113.0   25
                           lū[may]MOD:lū:lu-u                  47.0   15
                           lū[may]MOD:lū:lu-u₂                  6.0    2
šarru[king]N:šarri         šarru[king]N:šarri:LUGAL           374.0  173
                           šarru[king]N:šarri:MAN               1.0    3
šarru[king]N:šarru         šarru[king]N:šarru:LUGAL             NaN  240
                           šarru[king]N:šarru:MAN               NaN    1
šulmu[completeness]N:šulmu šulmu[completeness]N:šulmu:DI-mu   203.0   11
                           šulmu[completeness]N:šulmu:šul-mu   16.0    4

In [448]:
print('LUGAL appear ' + str(df_words[df_words['form'] == 'LUGAL'].shape[0]) + ' times (by itself)')
print('MAN appears ' + str(df_words[df_words['form'] == 'MAN'].shape[0]) + ' times (by itself)')

LUGAL appear 2753 times (by itself)
MAN appears 27 times (by itself)


In [451]:
df_MAN = pd.DataFrame(df_words[(df_words['form'].str.contains('MAN')) & (df_words['lemma'] == 'šarru[king]N')].groupby('text_id').agg('count')['cf'])
df_MAN

cf
text_id    
P224485   1
P313453   1
P313480   2
P313814   1
P314321   1
P334113   3
P334158   1
P334179   6
P334201   1
P334360   1
P334588   1
P334610   1
P334729   4
P334831   1
X900004   2
X900012   1

In [452]:
pd.concat([df_class.loc[list(df_MAN.index)],df_MAN],axis=1)

ancient_author designation        dossier dossier_nocertain  \
text_id                                                                         
P224485                Sargon II  SAA 01 001  SAA01.01.01.a       SAA01.01.01   
P313453          Ṭab-ṣill-Ešarra  SAA 05 291  SAA05.14.01.c       SAA05.14.01   
P313480  Nashir-Bel (Liphur-Bel)  SAA 05 015  SAA05.01.01.b       SAA05.01.01   
P313814           Nabu-duru-uṣur  SAA 15 129  SAA15.05.02.c       SAA15.05.02   
P314321                (unknown)  SAA 05 189  SAA05.09.01.c       SAA05.09.01   
P334113        Ina-šar-Bel-allak  SAA 01 128  SAA01.06.02.a       SAA01.06.02   
P334158                    Hunni  SAA 01 133  SAA01.07.01.a       SAA01.07.01   
P334179       Aššur-belu-uda’’an  SAA 05 126  SAA05.07.02.a       SAA05.07.02   
P334201           Šarru-emuranni  SAA 15 217  SAA15.07.01.a       SAA15.07.01   
P334360                Sin-ila’i  SAA 15 241  SAA15.07.03.a       SAA15.07.03   
P334588             Tariba-Issar  SAA 01 160  SAA01.07.17.a       SAA01.07.17   
P334610        Samnuha-belu-uṣur  SAA 01 224  SAA01.11.03.b       SAA01.11.03   
P334729        Ina-šar-Bel-allak  SAA 01 129  SAA01.06.02.c       SAA01.06.02   
P334831                (unknown)  SAA 05 256  SAA05.12.10.c       SAA05.12.10   
X900004                    Mahde  SAA 05 074  SAA05.05.01.a       SAA05.05.01   
X900012         Nabu-belu-ka’’in  SAA 15 084  SAA15.04.01.c       SAA15.04.01   

         saa_chap                      senderloc  cf  
text_id                                               
P224485  SAA01.01                    Royal Court   1  
P313453  SAA05.14                          Ashur   1  
P313480  SAA05.01                          Amidi   2  
P313814  SAA15.05                            Der   1  
P314321  SAA05.09           Northeastern Assyria   1  
P334113  SAA01.06                  Dur-Sharruken   3  
P334158  SAA01.07                        Nineveh   1  
P334179  SAA05.07                        Kurbail   6  
P334201  SAA15.07                        Babylon   1  
P334360  SAA15.07  Central or Southern Babylonia   1  
P334588  SAA01.07                        Assyria   1  
P334610  SAA01.11                     Shadikanni   1  
P334729  SAA01.06                  Dur-Sharruken   4  
P334831  SAA05.12           Northeastern Assyria   1  
X900004  SAA05.05                        Nineveh   2  
X900012  SAA15.04                  Kar-Sharrukin   1

Information for sender location

In [47]:
df_senderloc_certain = df_class[(df_class['senderloc'] != 'uncertain')]

list_senderloc_certain = list(df_senderloc_certain.index)

senderloc_tot = len(df_senderloc_certain['senderloc'].unique())
senderloc_tot

tm_senderloc_certain = tm_dist_all.loc[list(set(list_senderloc_certain) & set(list(tm_dist_all.index)))]
tm_senderloc_certain

NA:..    NA:.t.     NI:..    NI:.d.  bēlu[lord]N:bēlīya:EN-ia  \
P313635  0.000000  1.000000  1.000000  0.000000                  0.713624   
P313609  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313425  0.769231  0.230769  1.000000  0.000000                  1.000000   
P313995  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334210  1.000000  0.000000  1.000000  0.000000                  0.000000   
P334305  0.333333  0.666667  1.000000  0.000000                  1.000000   
P313483  1.000000  0.000000  1.000000  0.000000                  0.000000   
P334783  0.555556  0.444444  1.000000  0.000000                  1.000000   
P334139  1.000000  0.000000  1.000000  0.000000                  0.333333   
P334390  0.413793  0.586207  1.000000  0.000000                  0.333333   
P334676  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334709  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313934  1.000000  0.000000  0.946243  0.053757                  0.713624   
P313445  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334786  1.000000  0.000000  1.000000  0.000000                  1.000000   
P334673  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313821  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334165  1.000000  0.000000  1.000000  0.000000                  1.000000   
P334432  1.000000  0.000000  1.000000  0.000000                  0.333333   
P313476  0.500000  0.500000  0.615385  0.384615                  0.500000   
P313680  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334704  1.000000  0.000000  1.000000  0.000000                  0.713624   
P314195  0.852654  0.147346  0.946243  0.053757                  0.713624   
P334167  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313667  0.852654  0.147346  1.000000  0.000000                  0.713624   
P313640  1.000000  0.000000  0.555556  0.444444                  0.000000   
P313742  1.000000  0.000000  1.000000  0.000000                  1.000000   
P334296  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313738  1.000000  0.000000  0.875000  0.125000                  1.000000   
P334904  0.875000  0.125000  1.000000  0.000000                  1.000000   
...           ...       ...       ...       ...                       ...   
P334718  1.000000  0.000000  1.000000  0.000000                  1.000000   
P314187  0.852654  0.147346  0.946243  0.053757                  0.713624   
P314199  0.852654  0.147346  0.946243  0.053757                  0.713624   
P314301  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334055  1.000000  0.000000  1.000000  0.000000                  0.500000   
P314316  0.000000  1.000000  1.000000  0.000000                  0.713624   
P336769  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313527  0.666667  0.333333  1.000000  0.000000                  1.000000   
P334091  0.750000  0.250000  0.750000  0.250000                  0.713624   
P334587  1.000000  0.000000  1.000000  0.000000                  0.444444   
P313729  1.000000  0.000000  0.333333  0.666667                  0.713624   
P313788  1.000000  0.000000  1.000000  0.000000                  0.000000   
P334781  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334308  0.666667  0.333333  0.666667  0.333333                  1.000000   
P314245  1.000000  0.000000  0.750000  0.250000                  0.713624   
P334715  0.571429  0.428571  1.000000  0.000000                  1.000000   
P334332  0.357143  0.642857  1.000000  0.000000                  0.713624   
P314111  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334113  1.000000  0.000000  1.000000  0.000000                  0.713624   
P393866  0.750000  0.250000  1.000000  0.000000                  0.000000   
X900006 

Information for dossiers

In [48]:
df_dossier_certain_a = df_class[df_class['dossier'].str.contains('.a')]
df_dossier_certain_b = df_class[df_class['dossier'].str.contains('.b')]
df_dossier_certain_c = df_class[df_class['dossier'].str.contains('.c')]

list_dossier_certain_a = list(df_dossier_certain_a.index)
list_dossier_certain_b = list(df_dossier_certain_b.index)
list_dossier_certain_c = list(df_dossier_certain_c.index)

dossier_certain_a_tot = len(df_dossier_certain_a['dossier'].unique())
dossier_certain_b_tot = len(df_dossier_certain_b['dossier'].unique())
dossier_certain_c_tot = len(df_dossier_certain_c['dossier'].unique())

print(str(dossier_certain_a_tot) + ' unique dossiers in ' + str(len(list_dossier_certain_a)) + ' texts')
print(str(dossier_certain_b_tot) + ' unique dossiers in ' + str(len(list_dossier_certain_b)) + ' texts')
print(str(dossier_certain_c_tot) + ' unique dossiers in ' + str(len(list_dossier_certain_c)) + ' texts')
print(str(len(df_class['dossier_nocertain'].unique())))

106 unique dossiers in 276 texts
44 unique dossiers in 69 texts
93 unique dossiers in 609 texts
161


In [49]:
tm_dossier = tm_dist_all.loc[list(set(df_class.index) & set(list(tm_dist_all.index)))]
tm_dossier

NA:..    NA:.t.     NI:..    NI:.d.  bēlu[lord]N:bēlīya:EN-ia  \
P313635  0.000000  1.000000  1.000000  0.000000                  0.713624   
P313609  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313425  0.769231  0.230769  1.000000  0.000000                  1.000000   
P313995  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334210  1.000000  0.000000  1.000000  0.000000                  0.000000   
P334305  0.333333  0.666667  1.000000  0.000000                  1.000000   
P313483  1.000000  0.000000  1.000000  0.000000                  0.000000   
P334783  0.555556  0.444444  1.000000  0.000000                  1.000000   
P334139  1.000000  0.000000  1.000000  0.000000                  0.333333   
P334390  0.413793  0.586207  1.000000  0.000000                  0.333333   
P334676  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334709  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313934  1.000000  0.000000  0.946243  0.053757                  0.713624   
P313445  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334786  1.000000  0.000000  1.000000  0.000000                  1.000000   
P334673  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313821  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334165  1.000000  0.000000  1.000000  0.000000                  1.000000   
P334432  1.000000  0.000000  1.000000  0.000000                  0.333333   
P313476  0.500000  0.500000  0.615385  0.384615                  0.500000   
P313673  1.000000  0.000000  1.000000  0.000000                  0.666667   
P313680  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334704  1.000000  0.000000  1.000000  0.000000                  0.713624   
P314195  0.852654  0.147346  0.946243  0.053757                  0.713624   
P334167  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313667  0.852654  0.147346  1.000000  0.000000                  0.713624   
P313640  1.000000  0.000000  0.555556  0.444444                  0.000000   
P313742  1.000000  0.000000  1.000000  0.000000                  1.000000   
P313639  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334296  1.000000  0.000000  1.000000  0.000000                  1.000000   
...           ...       ...       ...       ...                       ...   
P336769  1.000000  0.000000  1.000000  0.000000                  0.713624   
P313527  0.666667  0.333333  1.000000  0.000000                  1.000000   
P334091  0.750000  0.250000  0.750000  0.250000                  0.713624   
P334587  1.000000  0.000000  1.000000  0.000000                  0.444444   
P334909  1.000000  0.000000  1.000000  0.000000                  0.333333   
P313852  1.000000  0.000000  0.666667  0.333333                  0.713624   
P313729  1.000000  0.000000  0.333333  0.666667                  0.713624   
P313788  1.000000  0.000000  1.000000  0.000000                  0.000000   
P334781  1.000000  0.000000  1.000000  0.000000                  0.713624   
P334308  0.666667  0.333333  0.666667  0.333333                  1.000000   
P314290  1.000000  0.000000  1.000000  0.000000                  0.713624   
P314245  1.000000  0.000000  0.750000  0.250000                  0.713624   
P334715  0.571429  0.428571  1.000000  0.000000                  1.000000   
P313955  0.500000  0.500000  1.000000  0.000000                  0.500000   
P334332  0.357143  0.642857  1.000000  0.000000                  0.713624   
P314111  0.852654  0.147346  1.000000  0.000000                  0.713624   
P334113  1.000000  0.000000  1.000000  0.000000                  0.713624   
P393866  0.750000  0.250000  1.000000  0.000000                  0.000000   
X900006  0.000000  1.000000  1.000000  0.000000                  0.713624   
P313931  0.852654  0.147346  0.946243  0.053757                  0.713624   
P313886 

Information for SAA chapters

In [50]:
saachap_tot = len(df_class['saa_chap'].unique())
saachap_tot

tm_saachap = tm_dist_all.loc[list(set(df_class.index) & set(list(tm_dist_all.index)))]
#tm_saachap
saachap_tot

37

Define the function for evaluation

In [51]:
from random import shuffle
def calculate_purity_score(dict_class,n):
    purity_score = 0
    for s in dict_class:
        cnt = Counter(dict_class[s])
        purity_score += cnt.most_common()[0][1]

    purity_score = purity_score / n
    return purity_score    

def labels_to_dict(labels,pnums):
    d = {}
    for i in range(len(labels)):
        d[pnums[i]] = labels[i]
    return d

In [304]:
def evaluate_clusters(tm_class,feature_list,flist_str,class_type,K,df_cl):
    list_evals = []
    c = 0
    for g in feature_list:
        c += 1
        print(str(c) + '. Evaluating: ' + str(g))
        km = KMeans(n_clusters=K,max_iter=1000).fit(tm_class[g])
        labels_random = km.labels_.copy()
        shuffle(labels_random)

        #Create Dictionary of cluster => list of pnums
        clustered = {}
        clustered_random = {}
        for i in range(len(km.labels_)):
            if km.labels_[i] in clustered:
                clustered[km.labels_[i]].append(df_cl.loc[tm_class.index[i]][class_type])
            else:
                clustered[km.labels_[i]] = [df_cl.loc[tm_class.index[i]][class_type]]
                
            if labels_random[i] in clustered_random:
                clustered_random[labels_random[i]].append(df_cl.loc[tm_class.index[i]][class_type])
            else:
                clustered_random[labels_random[i]] = [df_cl.loc[tm_class.index[i]][class_type]]
        
        #Create Dictionary of Pnum => cluster
        pnum_clusters = labels_to_dict(km.labels_,tm_class.index)
                
        #purity score
        purity_score_class = calculate_purity_score(clustered,len(tm_class.index))
        purity_score_random = calculate_purity_score(clustered_random,len(tm_class.index))
        
        d = {'group':g,
             'purity_class': purity_score_class,
             'purity_random': purity_score_random,
             'group_len': len(g),
             'class_type': class_type,
             'feature_type': flist_str,
             'num_clusters': K}
        list_evals.append(d)

    df_evals = pd.DataFrame(list_evals)
    #Error columns
    df_evals['error_sub'] = df_evals['purity_class'] - df_evals['purity_random']
    df_evals['error_div'] = df_evals['purity_class'] / df_evals['purity_random']
    df_evals.to_csv('output/evaluation_' + class_type + '_' + flist_str + '.csv',encoding='utf-8')
    return df_evals

In [56]:
df_evals_sender = evaluate_clusters(tm_senderloc_certain,list_power,'allpair','senderloc',senderloc_tot)
#df_evals_dossier = evaluate_clusters(tm_dossier,list_power,'allpair','dossier',len(df_class['dossier_nocertain'].unique()))
#df_evals_saachap = evaluate_clusters(tm_saachap,list_power,'allpair','saa_chap',saachap_tot)

1. Evaluating: ['NA:..', 'NA:.t.']
2. Evaluating: ['NI:..', 'NI:.d.']
3. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.']
4. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.']
5. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.']
6. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.']
7. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.']
8. Evaluating: ['ia', 'ia₂']
9. Evaluating: ['NA:..', 'NA:.t.', 'ia', 'ia₂']
10. Evaluating: ['NI:..', 'NI:.d.', 'ia', 'ia₂']
11. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'ia', 'ia₂']
12. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂']
13. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂']
14. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂']
15. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂']
16. Evaluating: ['ša', 'ša₂']
17. Evaluating: ['NA:..', 'NA:.t.', 

110. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂']
111. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂']
112. Evaluating: ['ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
113. Evaluating: ['NA:..', 'NA:.t.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
114. Evaluating: ['NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
115. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
116. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
117. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
118. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
119. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂']
120. Evaluating: ['ia', 'ia₂', 

178. Evaluating: ['NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
179. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
180. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
181. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
182. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
183. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
184. Evaluating: ['ia', 'ia₂', 'ša', 'ša₂', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīy

236. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
237. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
238. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
239. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
240. Evaluating: ['ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
241. Evaluating: ['NA:..', 'NA:.t.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia']
242. Evaluating: ['NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', '

302. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
303. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
304. Evaluating: ['ša', 'ša₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
305. Evaluating: ['NA:..', 'NA:.t.', 'ša', 'ša₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
306. Evaluating: ['NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
307. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'ša', 'ša₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
308. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
309. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a']
310. Evaluating: ['N

...

836. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
837. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
838. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
839. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
840. Evaluating: ['ia', 'ia₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
841. Evaluating: ['NA:..', 'NA:.t.', 'ia', 'ia₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
842. Evaluating: ['NI:..', 'NI:.d.', 'ia', 'ia₂', 'u', 'u₂', 

886. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
887. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
888. Evaluating: ['ia', 'ia₂', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
889. Evaluating: ['NA:..', 'NA:.t.', 'ia', 'ia₂', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
890. Evaluating: ['NI:..', 'NI:.d.', 'ia', 'ia₂', 'ša', 'ša₂', 'šu', 'šu₂', 'u', 'u₂', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
891. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'ia', 'ia₂', 'ša', 'ša₂', 'šu', 'šu₂', 'u', '

927. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'ša', 'ša₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
928. Evaluating: ['šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
929. Evaluating: ['NA:..', 'NA:.t.', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
930. Evaluating: ['NI:..', 'NI:.d.', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
931. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'šu', 'šu₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[m

964. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
965. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
966. Evaluating: ['NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
967. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
968. Evaluating: ['ia', 'ia₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be

1001. Evaluating: ['NA:..', 'NA:.t.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
1002. Evaluating: ['NI:..', 'NI:.d.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
1003. Evaluating: ['NA:..', 'NA:.t.', 'NI:..', 'NI:.d.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
1004. Evaluating: ['|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu', 'šu₂', 'u', 'u₂', 'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:be-li₂-ia', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:la-a', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u']
1005. Evaluating: ['NA:..', 'NA:.t.', '|ME.U.U.U|:..', '|ME.U.U.U|:.m.', 'ia', 'ia₂', 'šu

In [ ]:
df_evals_all = pd.concat([df_evals_sender_ortho_word,
                          df_evals_sender_ortho_sign,
                         df_evals_sender_paleo,
                          df_evals_dossier_ortho_word,
                          df_evals_dossier_ortho_sign,
                          df_evals_dossier_paleo,
                         df_evals_saachap_ortho_word,
                         df_evals_saachap_ortho_sign,
                         df_evals_saachap_paleo])
df_evals_all.to_csv('output/evaluation_all.csv',encoding='utf-8')

---LAS MATERIAL---

In [117]:
saa8_signs,saa8_words = parse_corpus('saa08')
saa10_signs,saa10_words = parse_corpus('saa10')

done
done


In [120]:
df_las_signs = pd.concat([pd.DataFrame(saa8_signs),pd.DataFrame(saa10_signs)])
df_las_signs = las_signs.fillna('')
df_las_signs

a            b    break         cf     epos f           file  \
0              1(diš)               no-cf  no-epos     P236880.json   
1                3(u)                 Sin       DN     P236880.json   
2                 ina                 ina      PRP     P236880.json   
3                 ITI              Addaru       MN     P236880.json   
4                  ŠE              Addaru       MN     P236880.json   
5                  UD                 ūmu        N     P236880.json   
6         1(u) 4(diš)               no-cf  no-epos     P236880.json   
7                KAM₂               no-cf  no-epos     P236880.json   
8                  lu                  lū      CNJ     P236880.json   
9                  UD                 ūmu        N     P236880.json   
10        1(u) 5(diš)               no-cf  no-epos     P236880.json   
11               KAM₂               no-cf  no-epos     P236880.json   
12                 KI                itti      PRP     P236880.json   
13               2(u)               Šamaš       DN     P236880.json   
14                 NU                  ul      MOD     P236880.json   
15                IGI               amāru        V     P236880.json   
16               NIG₂            šahluqtu        N     P236880.json   
17                 HA            šahluqtu        N     P236880.json   
18                LAM            šahluqtu        N     P236880.json   
19                 MA            šahluqtu        N     P236880.json   
20                ŠEŠ                 Uru       GN     P236880.json   
21               UNUG                 Uru       GN     P236880.json   
22                 KI                 Uru       GN     P236880.json   
23             1(diš)               no-cf  no-epos     P236880.json   
24               3(u)                 Sin       DN     P236880.json   
25                ina                 ina      PRP     P236880.json   
26                 la                  lā      MOD     P236880.json   
27                 si              simānu        N     P236880.json   
28                 ma              simānu        N     P236880.json   
29                 ni              simānu        N     P236880.json   
30                šu₂              simānu        N     P236880.json   
31                 uh               ahāru        V     P236880.json   
32                 hi               ahāru        V     P236880.json   
33                ram               ahāru        V     P236880.json   
34                 ma               ahāru        V     P236880.json   
35                 NU                  ul      MOD     P236880.json   
36                IGI               amāru        V     P236880.json   
37                 ZI                tebû        N     P236880.json   
38                  e                tebû        N     P236880.json   
39                URU                 ālu        N     P236880.json   
40                ŠU₂             kiššūtu        N     P236880.json   
41                tu₂             kiššūtu        N     P236880.json   
42                 MU               šattu        N     P236880.json   
43                MEŠ               šattu        N     P236880.json   
44                ša₂                  ša      DET     P236880.json   
45                                  no-cf  no-epos     P236880.json   
46                  x  missing      no-cf  no-epos     P236880.json   
47                 ru               no-cf  no-epos     P236880.json   
48             1(diš)               no-cf  no-epos     P236880.json   
49                 UD                 ūmu        N     P236880.json   
50        1(u) 6(diš)               no-cf  no-epos     P236880.json   
51               KAM₂               no-cf  no-epos     P236880.json   
52               3(u)                 Sin       DN     P236880.json   
53                  u                   u      CNJ     P236880.json   
54               2(u)               Šamaš       DN     P236880.json   
55                 KI          

In [122]:
file_names = df_las_signs['file'].unique()
df_las_signs['sign_form'] = df_las_signs['b'].apply(lambda x: sign_index.get(x.lower(),'?'))

import re
def get_num_part(s):
    try:
        n = re.findall(r'[₀₁₂₃₄₅₆₇₈₉]+',s)[0]
        n = n.replace('₀','0').replace('₁','1').replace('₂','2').replace('₃','3').replace('₄','4')
        n = n.replace('₅','5').replace('₆','6').replace('₇','7').replace('₈','8').replace('₉','9')
    except:
        n = 1
    return n

def get_str_part(s):
    try:
        n = re.findall(r'[a-zA-ZšŠṣṢṭṬʾ \(\)0-9]+',s)[0]
    except:
        n = s
    return n
        
df_las_signs['str_part'] = df_las_signs['b'].apply(lambda x: get_str_part(x))
df_las_signs['num_part'] = df_las_signs['b'].apply(lambda x: get_num_part(x))
#df['combined'] = df['sign_form'] + ':' + df['mods_str']
df_las_signs

a            b    break        cf     epos f           file  \
0              1(diš)              no-cf  no-epos     P236880.json   
1                3(u)                Sin       DN     P236880.json   
2                 ina                ina      PRP     P236880.json   
3                 ITI             Addaru       MN     P236880.json   
4                  ŠE             Addaru       MN     P236880.json   
5                  UD                ūmu        N     P236880.json   
6         1(u) 4(diš)              no-cf  no-epos     P236880.json   
7                KAM₂              no-cf  no-epos     P236880.json   
8                  lu                 lū      CNJ     P236880.json   
9                  UD                ūmu        N     P236880.json   
10        1(u) 5(diš)              no-cf  no-epos     P236880.json   
11               KAM₂              no-cf  no-epos     P236880.json   
12                 KI               itti      PRP     P236880.json   
13               2(u)              Šamaš       DN     P236880.json   
14                 NU                 ul      MOD     P236880.json   
15                IGI              amāru        V     P236880.json   
16               NIG₂           šahluqtu        N     P236880.json   
17                 HA           šahluqtu        N     P236880.json   
18                LAM           šahluqtu        N     P236880.json   
19                 MA           šahluqtu        N     P236880.json   
20                ŠEŠ                Uru       GN     P236880.json   
21               UNUG                Uru       GN     P236880.json   
22                 KI                Uru       GN     P236880.json   
23             1(diš)              no-cf  no-epos     P236880.json   
24               3(u)                Sin       DN     P236880.json   
25                ina                ina      PRP     P236880.json   
26                 la                 lā      MOD     P236880.json   
27                 si             simānu        N     P236880.json   
28                 ma             simānu        N     P236880.json   
29                 ni             simānu        N     P236880.json   
...   ..          ...      ...       ...      ... ..           ...   
79969               x  missing     no-cf  no-epos     P336680.json   
79970               x  missing     no-cf  no-epos     P336680.json   
79971               x  missing     no-cf  no-epos     P336680.json   
79972               x  missing     no-cf  no-epos     P336680.json   
79973               x  missing     no-cf  no-epos     P336680.json   
79974               x  missing     no-cf  no-epos     P336680.json   
79975               x  missing     no-cf  no-epos     P336680.json   
79976               x  missing     no-cf  no-epos     P336680.json   
79977               x  missing     no-cf  no-epos     P336680.json   
79978              TA               ištu      PRP     P336680.json   
79979            BAR₂  damaged    Barsip       GN     P336680.json   
79980            SIPA  missing    Barsip       GN     P336680.json   
79981              KI  missing    Barsip       GN     P336680.json   
79982               x  missing     no-cf  no-epos     P336680.json   
79983               x  missing     no-cf  no-epos     P336680.json   
79984               x  missing     no-cf  no-epos     P336680.json   
79985               x  missing     no-cf  no-epos     P336680.json   
79986               x  missing     no-cf  no-epos     P336680.json   
79987               x  missing     no-cf  no-epos     P336680.json   
79988               x  missing     no-cf  no-epos     P336680.json   
79989               x  missing     no-cf  no-epos     P336680.json   
79990               x  missing     no-cf  no-epos     P336680.json   
79991               x  missing     no-cf  no-epos     P336680.json   
79992                              no-cf  no-epos     P336680.json   
79993  v          LU₂              no-cf  no-epos     P336680.json   
79994            

In [123]:
df2 = pd.DataFrame(df_las_signs.groupby(['str_part'])['num_part'].agg('nunique'))
list_ortho_syls = list(df2[df2[('num_part')] > 1].index)

list_ortho_syls = [h for h in list_ortho_syls if len(re.findall(r'[A-Z]',h)) == 0]
list_ortho_syls

df_las_ortho_signs = df_las_signs[df_las_signs['str_part'].isin(list_ortho_syls)]
df_las_ortho_signs

a     b    break         cf     epos f           file  \
8          lu                  lū      CNJ     P236880.json   
26         la                  lā      MOD     P236880.json   
30        šu₂              simānu        N     P236880.json   
38          e                tebû        N     P236880.json   
41        tu₂             kiššūtu        N     P236880.json   
44        ša₂                  ša      DET     P236880.json   
53          u                   u      CNJ     P236880.json   
69        ša₂                  ša      DET     P236880.json   
73         pi               ṭuppu        N     P236880.json   
88         nu  missing  Ṣalbatanu       CN     P236880.json   
91        šu₂  missing      libbu        N     P236880.json   
101        me  missing     mērešu        N     P236880.json   
103       šu₂  missing     mērešu        N     P236880.json   
148        nu           Ṣalbatanu       CN     P236880.json   
165         e                šamû        N     P236880.json   
166        u₂              lapātu        V     P236880.json   
172        u₂                qatû        V     P236880.json   
173       qat                qatû        V     P236880.json   
179        nu           Ṣalbatanu       CN     P236880.json   
182        il              baʾālu        V     P236880.json   
186        u₂              lapātu        V     P236880.json   
190       ša₂                  ša      PRP     P236880.json   
193       ša₂             Ašaredu       PN     P236880.json   
197        u₂               mahrû       AJ     P236880.json   
199       ša₂                  ša      DET     P236880.json   
203         e                šamû        N     P236907.json   
213        ši                bašû        V     P236907.json   
216        la             Ṣillaya       PN     P236907.json   
224        il              šapāru        V     P236907.json   
230        mi              mītūtu        N     P236907.json   
...   ..  ...      ...        ...      ... ..           ...   
79830      nu              gamāru        V     P336679.json   
79835      su             issurri       AV     P336679.json   
79836      ur             issurri       AV     P336679.json   
79841      ša                  ša      DET     P336679.json   
79847     aš₂                bašû        V     P336679.json   
79848      ši                bašû        V     P336679.json   
79850       e                rēhu       AJ     P336679.json   
79853      pu               ṭuppu        N     P336679.json   
79854      ša                šanû       AJ     P336679.json   
79856      u₂                šanû       AJ     P336679.json   
79859      ap                ṭepû        V     P336679.json   
79860      pi                ṭepû        V     P336679.json   
79862     ša₂              šakānu        V     P336679.json   
79864     mi₃                mīnu       QP     P336679.json   
79866      nu                mīnu       QP     P336679.json   
79867      ša                  ša      REL     P336679.json   
79873     par              šapāru        V     P336679.json   
79876      ši  damaged     šapāru        V     P336679.json   
79882     ia₂  missing       bēlu        N     P336680.json   
79889      lu  missing         lū      MOD     P336680.json   
79890       u  missing         lū      MOD     P336680.json   
79897     ia₂                bēlu        N     P336680.json   
79900       u                   u      CNJ     P336680.json   
79908     ia₂  missing       bēlu        N     P336680.json   
79913      me                 ūmu        N     P336680.json   
79914     ar₂                arku       AJ     P336680.json   
79917      ṭu                ṭūbu        N     P336680.json   
79920       u  missing          u      CNJ     P336680.json   
79933     ia₂                bēlu        N     P336680.json   
79964     šu₂               no-cf  no-epos     P336680.json   

                        form                       frag                 gw  \
8                    

In [124]:
df_las_ortho_str = pd.DataFrame(df_las_ortho_signs.groupby(['text_id']).apply(lambda x: ' '.join(x['b'])))
df_las_ortho_str.columns = ['ortho_str']
df_las_ortho_str

cv = CountVectorizer(token_pattern='[^ ]+',lowercase=False)
ft = cv.fit_transform(list(df_las_ortho_str['ortho_str']))
tm_las_ortho_sign = pd.DataFrame(ft.toarray(),columns=cv.get_feature_names(),index=df_las_ortho_str.index)
tm_las_ortho_sign

ad  ad₂  ap  ap₂  ar  ar₂  as  as₂  aš  aš₂ ...   ʾa  ʾa₃  ṣu  ṣu₂  \
text_id                                              ...                      
P236880   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236907   2    0   0    0   0    0   0    0   0    1 ...    0    0   0    0   
P236915   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236916   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236917   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236918   0    0   0    0   0    0   0    0   0    0 ...    1    0   0    0   
P236919   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236920   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236921   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236922   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236933   1    0   0    0   0    2   0    0   0    0 ...    0    0   0    0   
P236939   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236942   0    0   0    0   0    0   0    0   0    0 ...    0    0   1    0   
P236944   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236949   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236957   0    0   0    0   0    1   0    0   0    1 ...    0    0   0    0   
P236964   0    0   0    0   0    1   0    0   0    0 ...    0    0   0    0   
P236966   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236967   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236968   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236969   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236970   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236971   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236972   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236973   0    0   0    0   0    0   0    0   0    1 ...    0    0   0    0   
P236976   0    0   0    0   0    0   0    0   0    1 ...    0    0   0    0   
P236977   0    0   0    0   0    0   0    0   0    1 ...    0    0   0    0   
P236978   1    0   0    0   1    0   0    0   0    0 ...    0    0   0    0   
P236979   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P236980   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
...      ..  ...  ..  ...  ..  ...  ..  ...  ..  ... ...   ..  ...  ..  ...   
P336592   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336593   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336594   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336652   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336653   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336654   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336655   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336656   0    1   0    0   0    0   2    0   0    1 ...    0    0   0    0   
P336657   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336658   0    0   0    0   0    0   0    0   0    1 ...    0    0   0    0   
P336659   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336660   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336661   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336662   0    0   0    0   0    0   0    0   1    0 ...    0    0   0    0   
P336663   0    0   0    0   0    0   0    0   1    1 ...    0    0   0    0   
P336664   0    0   0    0   0    0   0    0   0    0 ...    0    0   0    0   
P336666   0    0   0    0   0    0   0    0   0    1 ...    0    0   0    0   
P336667   0    0   0    0   0    0   0    0   0    0 ...   

In [264]:
df_las_words = pd.concat([pd.DataFrame(saa8_words),pd.DataFrame(saa10_words)])
df_las_words = df_las_words[(df_las_words['cf'] != 'no-cf')]

df_las_words['lemma'] = df_las_words['cf'] + '[' + df_las_words['gw'].apply(lambda x: x.replace(' ','-')) + ']' + df_las_words['pos']
df_las_words['lemma_norm'] = df_las_words['lemma'] + ':' + df_las_words['norm']
df_las_words['lemma_norm_form'] = df_las_words['lemma_norm'] + ':' + df_las_words['form']

df_norm_uniq = pd.DataFrame(df_las_words.groupby('lemma_norm')['form'].nunique())
list_ortho_words = list(df_norm_uniq[df_norm_uniq[('form')] > 1].index)

df_form_50 = pd.DataFrame(df_las_words.groupby('lemma_norm_form')['form'].agg('count'))
list_form_50 = list(df_form_50[df_form_50[('form')] > 50].index)

df_las_ortho_words = df_las_words[(df_las_words['lemma_norm'].isin(list_ortho_words)) & df_las_words['lemma_norm_form'].isin(list_form_50)]
df_las_ortho_words#[df_las_ortho_words['cf'] == 'ammar']

cf epos          file               form                 frag  \
1            Sin   DN  P236880.json                 30                   30   
2            ina  PRP  P236880.json                ina                  ina   
4            ūmu    N  P236880.json                 UD                   UD   
7            ūmu    N  P236880.json                 UD                   UD   
9           itti  PRP  P236880.json                 KI                   KI   
10         Šamaš   DN  P236880.json                 20                   20   
12         amāru    V  P236880.json                IGI                  IGI   
16           Sin   DN  P236880.json                 30                   30   
17           ina  PRP  P236880.json                ina                  ina   
18            lā  MOD  P236880.json                 la                   la   
22         amāru    V  P236880.json                IGI                  IGI   
27            ša  DET  P236880.json                ša₂                  ša₂   
31           ūmu    N  P236880.json                 UD                   UD   
33           Sin   DN  P236880.json                 30                   30   
34             u  CNJ  P236880.json                  u                    u   
35         Šamaš   DN  P236880.json                 20                   20   
36          itti  PRP  P236880.json                 KI                   KI   
38         amāru    V  P236880.json            IGI-MEŠ             IGI-MEŠ]   
39         šarru    N  P236880.json              LUGAL                LUGAL   
44            ša  DET  P236880.json                ša₂                  ša₂   
45         libbu    N  P236880.json             ŠA₃-bi               ŠA₃-bi   
53           Sin   DN  P236880.json                 30                   30   
54       tarbaṣu    N  P236880.json               TUR₃                 TUR₃   
56     Ṣalbatanu   CN  P236880.json  {MUL}ṣal-bat-a-nu   {mul}[ṣal-bat-a-nu   
57           ina  PRP  P236880.json                ina                  ina   
58         libbu    N  P236880.json            ŠA₃-šu₂              ŠA₃-šu₂   
59        izuzzu    V  P236880.json                GUB                 GUB]   
62           ina  PRP  P236880.json                ina                  ina   
63          mātu    N  P236880.json                KUR                  KUR   
68         ešēru    V  P236880.json             SI.SA₂              SI.[SA₂   
92           ana  PRP  P236880.json               a-na                 a-na   
97     Ṣalbatanu   CN  P236880.json  {MUL}ṣal-bat-a-nu  {[mul}ṣal]-bat-a-nu   
98           ana  PRP  P236880.json               a-na                 a-na   
104         šamû    N  P236880.json               AN-e                 AN-e   
106        šarru    N  P236880.json              LUGAL                LUGAL   
107         mātu    N  P236880.json            KUR.KUR              KUR.KUR   
113           ša  PRP  P236880.json                ša₂                  ša₂   
117           ša  DET  P236880.json                ša₂                  ša₂   
118        šarru    N  P236880.json              LUGAL                LUGAL   
120         šamû    N  P236907.json               AN-e                 AN-e   
124          ina  PRP  P236907.json                ina                  ina   
125         mātu    N  P236907.json                KUR                  KUR   
126         bašû    V  P236907.json            GAL₂-ši              GAL₂-ši   
128          ina  PRP  P236907.json                ina                  ina   
133          ana  PRP  P236907.json                ana                  ana   
146            u  CNJ  P236907.json                  u                    u   
147          Bel   DN  P236907.json              {d}EN               {d}⸢EN   
152          ina  PRP  P236907.json                ina                  ina   
153        libbu    N  P236907.json                ŠA₃                  ŠA₃   
157           kī  MOD  P236907.json               ki-i          

In [265]:
df_las_ortho_wordstr = pd.DataFrame(df_las_ortho_words.groupby(['text_id']).apply(lambda x: ' '.join(x['lemma_norm_form'])))
df_las_ortho_wordstr.columns = ['ortho_wordstr']
df_las_ortho_wordstr

cv = CountVectorizer(token_pattern='[^ ]+',lowercase=False)
ft = cv.fit_transform(list(df_las_ortho_wordstr['ortho_wordstr']))
tm_las_ortho_word = pd.DataFrame(ft.toarray(),columns=cv.get_feature_names(),index=df_las_ortho_wordstr.index)
#tm_las_ortho_word.to_csv('output/tm_ortho_word.csv',encoding='utf-8',sep='\t')
tm_las_ortho_word.columns

Index(['Bel[1]DN:Bel:{d}EN', 'Dilbat[Venus]CN:Dilbat:{MUL}dil-bat',
       'Marduk[1]DN:Marduk:{d}AMAR.UTU',
       'Mat-Akkadi[Babylonia]GN:Mat-Akkadi:KUR-URI{KI}',
       'Mat-Akkadi[Babylonia]GN:Mat-Akkadi:URI{KI}',
       'Mat-Amurri[Westland]GN:Mat-Amurri:KUR-MAR.TU{KI}',
       'Nabu[1]DN:Nabu:{d}AG', 'Nabu[1]DN:Nabu:{d}PA',
       'Sagmegar[Jupiter]CN:Sagmegar:{MUL}SAG.ME.GAR', 'Sin[1]DN:Sin:30',
       'Sin[1]DN:Sin:{d}30', 'abu[father]N:abīšu:AD-šu₂',
       'adi[until]PRP:adi:a-di', 'amāru[see]V:innamir:IGI',
       'amāru[see]V:innamir:IGI-ir', 'amāru[see]V:innamrū:IGI-MEŠ',
       'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana',
       'antalû[eclipse]N:attalû:AN.MI', 'anāku[I]IP:anāku:a-na-ku',
       'arku[long]AJ:arkūti:GID₂.DA-MEŠ', 'bašû[exist]V:ibašši:GAL₂-ši',
       'bašû[exist]V:ibašši:i-ba-aš₂-ši', 'bēlu[lord]N:bēlī:be-li',
       'bēlu[lord]N:bēlī:be-li₂', 'bēlu[lord]N:bēlīni:EN-ni',
       'bēlu[lord]N:bēlīya:EN-ia', 'bēlu[lord]N:bēlīya:EN-ia₂',
       'bēlu[lord]N:

In [267]:
tm_las_counts = pd.concat([tm_las_ortho_sign,tm_las_ortho_word],axis=1)
tm_las_counts

ad  ad₂   ap  ap₂   ar  ar₂   as  as₂   aš  aš₂  \
P236880  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236907  2.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P236915  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236916  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236917  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236918  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236919  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236920  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236921  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236922  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236933  1.0  0.0  0.0  0.0  0.0  2.0  0.0  0.0  0.0  0.0   
P236939  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236942  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236944  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236949  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236957  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  1.0   
P236964  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0   
P236966  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236967  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236968  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236969  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236970  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236971  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236972  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236973  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P236976  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P236977  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P236978  1.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0   
P236979  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236980  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236981  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236986  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  2.0   
P236987  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236988  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236989  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  1.0  1.0   
P236990  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236991  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236992  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0   
P236993  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236994  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P236995  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237007  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P237014  0.0  1.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0   
P237019  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237038  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0   
P237039  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237074  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237195  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237206  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237220  0.0  0.0  1.0  0.0  0.0  2.0  0.0  0.0  3.0  5.0   
P237226  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237234  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  1.0   
P237237  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  3.0   
P237247  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P237252  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P237270  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  1.0  6.0   
P237275  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0   
P237278  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0   
P237284  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  1.0   
P237285  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237286  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237287  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
P237288  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0   
P237289  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0   
P237290  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0

In [128]:
df_las_ortho_sign_count = pd.DataFrame(df_las_ortho_signs.groupby(['str_part','b'])['cf'].agg('count'))
df_las_ortho_sign_count = df_las_ortho_sign_count[df_las_ortho_sign_count[('cf')] > 100]

df_las_ortho_sign_uniq = df_las_ortho_sign_count.groupby([('str_part')]).nunique()

df_las_ortho_sign_count = df_las_ortho_sign_count.loc[list(df_las_ortho_sign_uniq[df_las_ortho_sign_uniq[('cf')] > 1].index)]
df_las_ortho_sign_count

cf
str_part b        
aš       aš    152
         aš₂   433
ia       ia   1169
         ia₂   471
li       li    629
         li₂   889
tu       tu    602
         tu₂   363
u        u    1955
         u₂   1755
         u₃    460
ša       ša   1454
         ša₂  1602
šu       šu    729
         šu₂  1847

In [129]:
df_las_ortho_word_count = pd.DataFrame(df_las_words.groupby(['lemma_norm','lemma_norm_form'])['cf'].agg('count'))
df_las_ortho_word_count = df_las_ortho_word_count[df_las_ortho_word_count[('cf')] > 50]

df_las_ortho_word_uniq = df_las_ortho_word_count.groupby([('lemma_norm')]).nunique()

df_las_ortho_word_count = df_las_ortho_word_count.loc[list(df_las_ortho_word_uniq[df_las_ortho_word_uniq[('cf')] > 1].index)]
df_las_ortho_word_count

cf
lemma_norm                         lemma_norm_form                                     
Mat-Akkadi[Babylonia]GN:Mat-Akkadi Mat-Akkadi[Babylonia]GN:Mat-Akkadi:KUR-URI{KI}   178
                                   Mat-Akkadi[Babylonia]GN:Mat-Akkadi:URI{KI}        60
Nabu[1]DN:Nabu                     Nabu[1]DN:Nabu:{d}AG                             208
                                   Nabu[1]DN:Nabu:{d}PA                             168
Sin[1]DN:Sin                       Sin[1]DN:Sin:30                                  744
                                   Sin[1]DN:Sin:{d}30                               331
amāru[see]V:innamir                amāru[see]V:innamir:IGI                           95
                                   amāru[see]V:innamir:IGI-ir                        86
ana[to]PRP:ana                     ana[to]PRP:ana:a-na                             1905
                                   ana[to]PRP:ana:ana                               376
bašû[exist]V:ibašši                bašû[exist]V:ibašši:GAL₂-ši                      115
                                   bašû[exist]V:ibašši:i-ba-aš₂-ši                   53
bēlu[lord]N:bēlī                   bēlu[lord]N:bēlī:be-li                            58
                                   bēlu[lord]N:bēlī:be-li₂                          358
bēlu[lord]N:bēlīya                 bēlu[lord]N:bēlīya:EN-ia                         513
                                   bēlu[lord]N:bēlīya:EN-ia₂                        362
                                   bēlu[lord]N:bēlīya:be-li₂-ia                     392
                                   bēlu[lord]N:bēlīya:be-li₂-ia₂                     77
ina[in]PRP:ina                     ina[in]PRP:ina:i-na                               57
                                   ina[in]PRP:ina:ina                              2716
itti[with]PRP:itti                 itti[with]PRP:itti:KI                            201
                                   itti[with]PRP:itti:it-ti                          83
izuzzu[stand]V:izziz               izuzzu[stand]V:izziz:GUB                          95
                                   izuzzu[stand]V:izziz:GUB-iz                       80
libbu[interior]N:libbi             libbu[interior]N:libbi:ŠA₃                       347
                                   libbu[interior]N:libbi:ŠA₃-bi                    306
lā[not]MOD:lā                      lā[not]MOD:lā:NU                                  87
                                   lā[not]MOD:lā:la                                 526
lū[may]MOD:lū                      lū[may]MOD:lū:lu                                 221
                                   lū[may]MOD:lū:lu-u                               237
muhhu[skull]N:muhhi                muhhu[skull]N:muhhi:UGU                          339
                                   muhhu[skull]N:muhhi:UGU-hi                        68
māru[son]N:mār                     māru[son]N:mār:DUMU                              120
                                   māru[son]N:mār:DUMU-LUGAL                         67
nakru[strange]AJ:nakri             nakru[strange]AJ:nakri:KUR₂                       64
                                   nakru[strange]AJ:nakri:{LU₂}KUR₂                  57
pānu[front]N:pān                   pānu[front]N:pān:IGI                             147
                                   pānu[front]N:pān:pa-an                           102
u[and]CNJ:u                        u[and]CNJ:u:u                                    747
                                   u[and]CNJ:u:u₃                                   460
Šamaš[1]DN:Šamaš                   Šamaš[1]DN:Šamaš:20                              214
                                   Šamaš[1]DN:Šamaš:{d}UTU                          295
ša[of]DET:ša                       ša[of]DET:ša:ša                                  901
                                   ša[of]DET:ša:ša₂                                 756
ša[that]REL:ša                     ša

In [269]:
#Orthography - Sign
map_ortho_sign = {'aš':['aš','aš₂'],
                  'ia':['ia','ia₂'],
                  'li':['li','li₂'],
                  'ša':['ša','ša₂'],
                  'šu':['šu','šu₂'],
                  'tu':['tu','tu₂'],
                  'u':['u','u₂']
                 }
list_ortho_sign = []
list_ortho_sign_pairs = []
for v in map_ortho_sign.values():
    list_ortho_sign = list_ortho_sign + v
    list_ortho_sign_pairs.append(v)
list_ortho_sign

#Orthography - Word
map_ortho_word = {'Sin[1]DN:Sin':['Sin[1]DN:Sin:30','Sin[1]DN:Sin:{d}30'],
                  'ana[to]PRP:ana':['ana[to]PRP:ana:a-na','ana[to]PRP:ana:ana'],
                  'libbu[interior]N:libbi':['libbu[interior]N:libbi:ŠA₃','libbu[interior]N:libbi:ŠA₃-bi'],
                  'lā[not]MOD:lā':['lā[not]MOD:lā:la','lā[not]MOD:lā:NU'],
                  'lū[may]MOD:lū':['lū[may]MOD:lū:lu','lū[may]MOD:lū:lu-u'],
                  #'mā[saying]PRP:mā':['mā[saying]PRP:mā:ma','mā[saying]PRP:mā:ma-a'],
                  'muhhu[skull]N:muhhi':['muhhu[skull]N:muhhi:UGU','muhhu[skull]N:muhhi:UGU-hi'],
                  'u[and]CNJ:u':['u[and]CNJ:u:u','u[and]CNJ:u:u₃'],
                  'ša[of]DET:ša':['ša[of]DET:ša:ša','ša[of]DET:ša:ša₂'],
                  'šulmu[completeness]N:šulmu':['šulmu[completeness]N:šulmu:DI-mu','šulmu[completeness]N:šulmu:šul-mu'],
                'šarru[king]N:šarru':['šarru[king]N:šarru:LUGAL','šarru[king]N:šarru:MAN']
                }
list_ortho_word = []
list_ortho_word_pairs = []
for v in map_ortho_word.values():
    list_ortho_word = list_ortho_word + v
    list_ortho_word_pairs.append(v)
list_ortho_word_pairs
list_features_all = list_ortho_sign + list_ortho_word
list_pairs_all = list_ortho_sign_pairs + list_ortho_word_pairs
list_features_all

['aš',
 'aš₂',
 'ia',
 'ia₂',
 'li',
 'li₂',
 'ša',
 'ša₂',
 'šu',
 'šu₂',
 'tu',
 'tu₂',
 'u',
 'u₂',
 'Sin[1]DN:Sin:30',
 'Sin[1]DN:Sin:{d}30',
 'ana[to]PRP:ana:a-na',
 'ana[to]PRP:ana:ana',
 'libbu[interior]N:libbi:ŠA₃',
 'libbu[interior]N:libbi:ŠA₃-bi',
 'lā[not]MOD:lā:la',
 'lā[not]MOD:lā:NU',
 'lū[may]MOD:lū:lu',
 'lū[may]MOD:lū:lu-u',
 'muhhu[skull]N:muhhi:UGU',
 'muhhu[skull]N:muhhi:UGU-hi',
 'u[and]CNJ:u:u',
 'u[and]CNJ:u:u₃',
 'ša[of]DET:ša:ša',
 'ša[of]DET:ša:ša₂',
 'šulmu[completeness]N:šulmu:DI-mu',
 'šulmu[completeness]N:šulmu:šul-mu',
 'šarru[king]N:šarru:LUGAL',
 'šarru[king]N:šarru:MAN']

In [292]:
map_all = map_ortho_sign.copy()
map_all.update(map_ortho_word)
map_all

{'Sin[1]DN:Sin': ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30'],
 'ana[to]PRP:ana': ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana'],
 'aš': ['aš', 'aš₂'],
 'ia': ['ia', 'ia₂'],
 'li': ['li', 'li₂'],
 'libbu[interior]N:libbi': ['libbu[interior]N:libbi:ŠA₃',
  'libbu[interior]N:libbi:ŠA₃-bi'],
 'lā[not]MOD:lā': ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU'],
 'lū[may]MOD:lū': ['lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u'],
 'muhhu[skull]N:muhhi': ['muhhu[skull]N:muhhi:UGU',
  'muhhu[skull]N:muhhi:UGU-hi'],
 'tu': ['tu', 'tu₂'],
 'u': ['u', 'u₂'],
 'u[and]CNJ:u': ['u[and]CNJ:u:u', 'u[and]CNJ:u:u₃'],
 'ša': ['ša', 'ša₂'],
 'ša[of]DET:ša': ['ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂'],
 'šarru[king]N:šarru': ['šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN'],
 'šu': ['šu', 'šu₂'],
 'šulmu[completeness]N:šulmu': ['šulmu[completeness]N:šulmu:DI-mu',
  'šulmu[completeness]N:šulmu:šul-mu']}

In [294]:
df_form_count = pd.DataFrame(df_las_words[df_las_words['lemma_norm_form'].isin(list_ortho_word)].
                             groupby(['lemma_norm','lemma_norm_form'])['cf'].agg('count'))
df_form_count

dict_form_count = {}
for ln in map_ortho_word:
    count1 = float(df_form_count.loc[(ln,map_ortho_word[ln][0])]['cf'])
    count2 = float(df_form_count.loc[(ln,map_ortho_word[ln][1])]['cf'])
    tot12 = count1 + count2
    dict_form_count[map_ortho_word[ln][0]] = count1 / tot12
    dict_form_count[map_ortho_word[ln][1]] = count2 / tot12
dict_form_count

df_sign_count = pd.DataFrame(df_las_signs[df_las_signs['b'].isin(list_ortho_sign)].groupby(['str_part','b'])['cf'].agg('count'))
df_sign_count

dict_sign_count = {}
for ln in map_ortho_sign:
    count1 = float(df_sign_count.loc[(ln,map_ortho_sign[ln][0])]['cf'])
    count2 = float(df_sign_count.loc[(ln,map_ortho_sign[ln][1])]['cf'])
    tot12 = count1 + count2
    dict_sign_count[map_ortho_sign[ln][0]] = count1 / tot12
    dict_sign_count[map_ortho_sign[ln][1]] = count2 / tot12
dict_sign_count

{'aš': 0.25982905982905985,
 'aš₂': 0.7401709401709402,
 'ia': 0.7128048780487805,
 'ia₂': 0.2871951219512195,
 'li': 0.41436100131752307,
 'li₂': 0.5856389986824769,
 'tu': 0.6238341968911917,
 'tu₂': 0.3761658031088083,
 'u': 0.5269541778975741,
 'u₂': 0.47304582210242585,
 'ša': 0.4757853403141361,
 'ša₂': 0.5242146596858639,
 'šu': 0.2829968944099379,
 'šu₂': 0.7170031055900621}

In [295]:
dict_count_all = dict_sign_count.copy()
dict_count_all.update(dict_form_count)
dict_count_all

{'Sin[1]DN:Sin:30': 0.6920930232558139,
 'Sin[1]DN:Sin:{d}30': 0.30790697674418605,
 'ana[to]PRP:ana:a-na': 0.8351600175361683,
 'ana[to]PRP:ana:ana': 0.16483998246383166,
 'aš': 0.25982905982905985,
 'aš₂': 0.7401709401709402,
 'ia': 0.7128048780487805,
 'ia₂': 0.2871951219512195,
 'li': 0.41436100131752307,
 'libbu[interior]N:libbi:ŠA₃': 0.5313935681470138,
 'libbu[interior]N:libbi:ŠA₃-bi': 0.4686064318529862,
 'li₂': 0.5856389986824769,
 'lā[not]MOD:lā:NU': 0.14192495921696574,
 'lā[not]MOD:lā:la': 0.8580750407830342,
 'lū[may]MOD:lū:lu': 0.48253275109170307,
 'lū[may]MOD:lū:lu-u': 0.517467248908297,
 'muhhu[skull]N:muhhi:UGU': 0.8329238329238329,
 'muhhu[skull]N:muhhi:UGU-hi': 0.16707616707616707,
 'tu': 0.6238341968911917,
 'tu₂': 0.3761658031088083,
 'u': 0.5269541778975741,
 'u[and]CNJ:u:u': 0.6188898094449047,
 'u[and]CNJ:u:u₃': 0.38111019055509526,
 'u₂': 0.47304582210242585,
 'ša': 0.4757853403141361,
 'ša[of]DET:ša:ša': 0.5437537718768859,
 'ša[of]DET:ša:ša₂': 0.456246228123

In [297]:
tm_dist_all = form_dist_matrix(tm_las_counts,map_all)
tm_dist_all

Sin[1]DN:Sin:30  Sin[1]DN:Sin:{d}30  ana[to]PRP:ana:a-na  \
P236880         1.000000            0.000000             1.000000   
P236907              NaN                 NaN             0.333333   
P236915         1.000000            0.000000                  NaN   
P236916              NaN                 NaN             1.000000   
P236917         1.000000            0.000000             0.000000   
P236918         1.000000            0.000000             1.000000   
P236919         0.666667            0.333333                  NaN   
P236920         1.000000            0.000000             0.500000   
P236921         0.800000            0.200000                  NaN   
P236922         1.000000            0.000000                  NaN   
P236933         1.000000            0.000000             0.166667   
P236939         1.000000            0.000000             0.857143   
P236942         1.000000            0.000000                  NaN   
P236944         1.000000            0.000000                  NaN   
P236949              NaN                 NaN                  NaN   
P236957         1.000000            0.000000             0.400000   
P236964              NaN                 NaN             0.857143   
P236966         1.000000            0.000000             0.000000   
P236967         1.000000            0.000000                  NaN   
P236968         1.000000            0.000000                  NaN   
P236969         1.000000            0.000000                  NaN   
P236970         1.000000            0.000000             0.000000   
P236971              NaN                 NaN                  NaN   
P236972              NaN                 NaN             1.000000   
P236973              NaN                 NaN             1.000000   
P236976         0.750000            0.250000             0.000000   
P236977         1.000000            0.000000             0.000000   
P236978         1.000000            0.000000             0.666667   
P236979              NaN                 NaN             1.000000   
P236980              NaN                 NaN                  NaN   
P236981              NaN                 NaN                  NaN   
P236986              NaN                 NaN             1.000000   
P236987         1.000000            0.000000             1.000000   
P236988         1.000000            0.000000             0.000000   
P236989              NaN                 NaN             0.000000   
P236990         0.666667            0.333333                  NaN   
P236991              NaN                 NaN                  NaN   
P236992         1.000000            0.000000             1.000000   
P236993         1.000000            0.000000             0.000000   
P236994              NaN                 NaN                  NaN   
P236995         1.000000            0.000000                  NaN   
P237007         1.000000            0.000000             0.000000   
P237014         1.000000            0.000000                  NaN   
P237019              NaN                 NaN                  NaN   
P237038         1.000000            0.000000             0.000000   
P237039         0.000000            1.000000             1.000000   
P237074              NaN                 NaN                  NaN   
P237195              NaN                 NaN                  NaN   
P237206              NaN                 NaN                  NaN   
P237220              NaN                 NaN             0.843750   
P237226         1.000000            0.000000                  NaN   
P237234         0.000000            1.000000             1.000000   
P237237         0.000000            1.000000             0.750000   
P237247         0.666667            0.333333             0.000000   
P237252              NaN                 NaN             1.000000   
P237270              NaN                 NaN             1.000000   
P237275              NaN                 NaN             1.000000   
P237278

In [298]:
for lnf in dict_count_all:
    #print(dict_form_count[lnf])
    tm_dist_all[lnf] = tm_dist_all[lnf].fillna(dict_count_all[lnf])
tm_dist_all

Sin[1]DN:Sin:30  Sin[1]DN:Sin:{d}30  ana[to]PRP:ana:a-na  \
P236880         1.000000            0.000000             1.000000   
P236907         0.692093            0.307907             0.333333   
P236915         1.000000            0.000000             0.835160   
P236916         0.692093            0.307907             1.000000   
P236917         1.000000            0.000000             0.000000   
P236918         1.000000            0.000000             1.000000   
P236919         0.666667            0.333333             0.835160   
P236920         1.000000            0.000000             0.500000   
P236921         0.800000            0.200000             0.835160   
P236922         1.000000            0.000000             0.835160   
P236933         1.000000            0.000000             0.166667   
P236939         1.000000            0.000000             0.857143   
P236942         1.000000            0.000000             0.835160   
P236944         1.000000            0.000000             0.835160   
P236949         0.692093            0.307907             0.835160   
P236957         1.000000            0.000000             0.400000   
P236964         0.692093            0.307907             0.857143   
P236966         1.000000            0.000000             0.000000   
P236967         1.000000            0.000000             0.835160   
P236968         1.000000            0.000000             0.835160   
P236969         1.000000            0.000000             0.835160   
P236970         1.000000            0.000000             0.000000   
P236971         0.692093            0.307907             0.835160   
P236972         0.692093            0.307907             1.000000   
P236973         0.692093            0.307907             1.000000   
P236976         0.750000            0.250000             0.000000   
P236977         1.000000            0.000000             0.000000   
P236978         1.000000            0.000000             0.666667   
P236979         0.692093            0.307907             1.000000   
P236980         0.692093            0.307907             0.835160   
P236981         0.692093            0.307907             0.835160   
P236986         0.692093            0.307907             1.000000   
P236987         1.000000            0.000000             1.000000   
P236988         1.000000            0.000000             0.000000   
P236989         0.692093            0.307907             0.000000   
P236990         0.666667            0.333333             0.835160   
P236991         0.692093            0.307907             0.835160   
P236992         1.000000            0.000000             1.000000   
P236993         1.000000            0.000000             0.000000   
P236994         0.692093            0.307907             0.835160   
P236995         1.000000            0.000000             0.835160   
P237007         1.000000            0.000000             0.000000   
P237014         1.000000            0.000000             0.835160   
P237019         0.692093            0.307907             0.835160   
P237038         1.000000            0.000000             0.000000   
P237039         0.000000            1.000000             1.000000   
P237074         0.692093            0.307907             0.835160   
P237195         0.692093            0.307907             0.835160   
P237206         0.692093            0.307907             0.835160   
P237220         0.692093            0.307907             0.843750   
P237226         1.000000            0.000000             0.835160   
P237234         0.000000            1.000000             1.000000   
P237237         0.000000            1.000000             0.750000   
P237247         0.666667            0.333333             0.000000   
P237252         0.692093            0.307907             1.000000   
P237270         0.692093            0.307907             1.000000   
P237275         0.692093            0.307907             1.000000   
P237278

In [238]:
cat_file08 = codecs.open('saa08/catalogue.json','r','utf-8')
cat_file10 = codecs.open('saa10/catalogue.json','r','utf-8')
cat_json08 = json.load(cat_file08)
cat_json10 = json.load(cat_file10)

class_l = []
class_index = []
for pnum in cat_json08['members']:
    id_text        = cat_json08['members'][pnum].get('id_text','')
    designation    = cat_json08['members'][pnum].get('designation','')
    ancient_author = cat_json08['members'][pnum].get('ancient_author','')
    class_d = {'designation': designation,'ancient_author':ancient_author}
    class_index.append(id_text)
    class_l.append(class_d)

for pnum in cat_json10['members']:
    id_text        = cat_json10['members'][pnum].get('id_text','')
    designation    = cat_json10['members'][pnum].get('designation','')
    ancient_author = cat_json10['members'][pnum].get('ancient_author','')
    class_d = {'designation': designation,'ancient_author':ancient_author}
    class_index.append(id_text)
    class_l.append(class_d)

df_class_las = pd.DataFrame(class_l,index=class_index)
df_class_las

ancient_author designation
P236880                                Ašaredu the Older  SAA 08 327
P236907                                            Zakir  SAA 08 309
P236915                                  Nabu-šuma-iškun  SAA 08 376
P236916                              Ašaredu the Younger  SAA 08 338
P236917                                            Zakir  SAA 08 303
P236918                                           Šumaya  SAA 08 499
P236919                              Ašaredu the Younger  SAA 08 345
P236920                                     (unassigned)  SAA 08 505
P236921                                     (unassigned)  SAA 08 508
P236922                                  Nabu-šuma-iškun  SAA 08 375
P236933                                     (unassigned)  SAA 08 535
P236939                               Nabu-iqbi of Cutha  SAA 08 422
P236942                                     (unassigned)  SAA 08 514
P236944                                  Nabu-ahhe-iddin  SAA 08 478
P236949                                     (unassigned)  SAA 08 550
P236957                               Šapiku of Borsippa  SAA 08 491
P236966                                        Bel-naṣir  SAA 08 466
P236967                                           Aplaya  SAA 08 360
P236968                                 Rašil (no title)  SAA 08 412
P236969                                   Bel-ahhe-eriba  SAA 08 454
P236970                                           Ṭabiya  SAA 08 439
P236971                                     (unassigned)  SAA 08 504
P236972                                           Nadinu  SAA 08 486
P236976                                  Nabu-šuma-iškun  SAA 08 371
P236977                                      Nergal-eṭir  SAA 08 257
P236978                           Nabu-iqiša of Borsippa  SAA 08 296
P236979                                Ašaredu the Older  SAA 08 334
P236980                                 Rašil (no title)  SAA 08 413
P236981                           Nabu-iqiša of Borsippa  SAA 08 289
P236986                                Ašaredu the Older  SAA 08 325
P236987                               Šapiku of Borsippa  SAA 08 492
P236988                              Ašaredu the Younger  SAA 08 351
P236989                                      Nergal-eṭir  SAA 08 245
P236990                                      Nergal-eṭir  SAA 08 261
P236991                                           Aplaya  SAA 08 368
P236992                               Nabu-iqbi of Cutha  SAA 08 429
P236993                                     (unassigned)  SAA 08 548
P236994                                            Zakir  SAA 08 313
P236995                                           Aplaya  SAA 08 364
P237007                               Nabu-iqbi of Cutha  SAA 08 427
P237014                                     (unassigned)  SAA 08 511
P237019                               Šapiku of Borsippa  SAA 08 496
P237038                                     (unassigned)  SAA 08 522
P237074                                      Nergal-eṭir  SAA 08 246
P237195                                     (unassigned)  SAA 08 560
P237206                                        Bel-naṣir  SAA 08 468
P237226                                   Ahheša of Uruk  SAA 08 451
P237247                           Nabu-iqiša of Borsippa  SAA 08 293
P237284                                      Nergal-eṭir  SAA 08 271
P237285                                      Nergal-eṭir  SAA 08 282
P237286                                      Nergal-eṭir  SAA 08 265
P237287                                Ašaredu the Older  SAA 08 335
P237288                              Ašaredu the Younger  SAA 08 343
P237289                              Ašaredu the Younger  SAA 08 353
P237290                                Ašaredu the Older  SAA 08 332
P237291                              Ašaredu the Younger  SAA 08 340
P237292                                           Ṭabiya  SAA 08 438
P237293                                 

In [302]:
df_author_certain = df_class_las[(df_class_las['ancient_author'] != '(unassigned)')]

list_author_certain = list(df_author_certain.index)

author_tot = len(df_author_certain['ancient_author'].unique())
#author_tot

tm_author_certain = tm_dist_all.loc[list(set(list_author_certain) & set(list(tm_dist_all.index)))]
#tm_author_certain
print('Total Authors: ' + str(author_tot) + ' in ' + str(len(tm_author_certain.index)) + ' Texts')

Total Authors: 100 in 800 Texts


In [272]:
tm_counts_class_las = pd.concat([tm_las_counts[list_features_all],df_class_las],axis=1)
tm_counts_class_las.to_csv('output/tm_counts_las.csv',encoding='utf-8')

tm_counts_class_author = pd.DataFrame(tm_counts_class_las.groupby('ancient_author').agg('sum'))[list_features_all]
tm_counts_class_author.to_csv('output/tm_counts_author_las.csv',encoding='utf-8')

In [291]:
import itertools
list_power = p(list_ortho_word_pairs)
list_power = [list(itertools.chain.from_iterable(x)) for x in list_power if x != []]
len(list_power)

1023

In [306]:
evaluate_clusters(tm_author_certain,list_power,'ortho_word_las','ancient_author',author_tot,df_class_las)

1. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30']
2. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana']
3. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana']
4. Evaluating: ['libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi']
5. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi']
6. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi']
7. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi']
8. Evaluating: ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU']
9. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU']
10. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU']
11. Evaluating: ['Sin[1]DN:Sin:30', '

56. Evaluating: ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi']
57. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi']
58. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi']
59. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi']
60. Evaluating: ['libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:

102. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃']
103. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃']
104. Evaluating: ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃']
105. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃']
106. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[an

143. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
144. Evaluating: ['lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
145. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
146. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
147. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
148. Evaluating: ['libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
149. Evaluating: ['Sin[1

183. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
184. Evaluating: ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
185. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
186. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂']
187. Evaluating: ['Si

...

950. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
951. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
952. Evaluating: ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'ša[of]DET:ša:ša', '

974. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
975. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
976. Evaluating: ['lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarr

998. Evaluating: ['ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
999. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
1000. Evaluating: ['lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', '

1019. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'ana[to]PRP:ana:a-na', 'ana[to]PRP:ana:ana', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
1020. Evaluating: ['libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lā[not]MOD:lā:la', 'lā[not]MOD:lā:NU', 'lū[may]MOD:lū:lu', 'lū[may]MOD:lū:lu-u', 'muhhu[skull]N:muhhi:UGU', 'muhhu[skull]N:muhhi:UGU-hi', 'u[and]CNJ:u:u', 'u[and]CNJ:u:u₃', 'ša[of]DET:ša:ša', 'ša[of]DET:ša:ša₂', 'šulmu[completeness]N:šulmu:DI-mu', 'šulmu[completeness]N:šulmu:šul-mu', 'šarru[king]N:šarru:LUGAL', 'šarru[king]N:šarru:MAN']
1021. Evaluating: ['Sin[1]DN:Sin:30', 'Sin[1]DN:Sin:{d}30', 'libbu[interior]N:libbi:ŠA₃', 'libbu[interior]N:libbi:ŠA₃-bi', 'lā[not]MO

class_type    feature_type  \
0     ancient_author  ortho_word_las   
1     ancient_author  ortho_word_las   
2     ancient_author  ortho_word_las   
3     ancient_author  ortho_word_las   
4     ancient_author  ortho_word_las   
5     ancient_author  ortho_word_las   
6     ancient_author  ortho_word_las   
7     ancient_author  ortho_word_las   
8     ancient_author  ortho_word_las   
9     ancient_author  ortho_word_las   
10    ancient_author  ortho_word_las   
11    ancient_author  ortho_word_las   
12    ancient_author  ortho_word_las   
13    ancient_author  ortho_word_las   
14    ancient_author  ortho_word_las   
15    ancient_author  ortho_word_las   
16    ancient_author  ortho_word_las   
17    ancient_author  ortho_word_las   
18    ancient_author  ortho_word_las   
19    ancient_author  ortho_word_las   
20    ancient_author  ortho_word_las   
21    ancient_author  ortho_word_las   
22    ancient_author  ortho_word_las   
23    ancient_author  ortho_word_las   
24    ancient_author  ortho_word_las   
25    ancient_author  ortho_word_las   
26    ancient_author  ortho_word_las   
27    ancient_author  ortho_word_las   
28    ancient_author  ortho_word_las   
29    ancient_author  ortho_word_las   
30    ancient_author  ortho_word_las   
31    ancient_author  ortho_word_las   
32    ancient_author  ortho_word_las   
33    ancient_author  ortho_word_las   
34    ancient_author  ortho_word_las   
35    ancient_author  ortho_word_las   
36    ancient_author  ortho_word_las   
37    ancient_author  ortho_word_las   
38    ancient_author  ortho_word_las   
39    ancient_author  ortho_word_las   
40    ancient_author  ortho_word_las   
41    ancient_author  ortho_word_las   
42    ancient_author  ortho_word_las   
43    ancient_author  ortho_word_las   
44    ancient_author  ortho_word_las   
45    ancient_author  ortho_word_las   
46    ancient_author  ortho_word_las   
47    ancient_author  ortho_word_las   
48    ancient_author  ortho_word_las   
49    ancient_author  ortho_word_las   
50    ancient_author  ortho_word_las   
51    ancient_author  ortho_word_las   
52    ancient_author  ortho_word_las   
53    ancient_author  ortho_word_las   
54    ancient_author  ortho_word_las   
55    ancient_author  ortho_word_las   
56    ancient_author  ortho_word_las   
57    ancient_author  ortho_word_las   
58    ancient_author  ortho_word_las   
59    ancient_author  ortho_word_las   
60    ancient_author  ortho_word_las   
61    ancient_author  ortho_word_las   
62    ancient_author  ortho_word_las   
63    ancient_author  ortho_word_las   
64    ancient_author  ortho_word_las   
65    ancient_author  ortho_word_las   
66    ancient_author  ortho_word_las   
67    ancient_author  ortho_word_las   
68    ancient_author  ortho_word_las   
69    ancient_author  ortho_word_las   
70    ancient_author  ortho_word_las   
71    ancient_author  ortho_word_las   
72    ancient_author  ortho_word_las   
73    ancient_author  ortho_word_las   
74    ancient_author  ortho_word_las   
75    ancient_author  ortho_word_las   
76    ancient_author  ortho_word_las   
77    ancient_author  ortho_word_las   
78    ancient_author  ortho_word_las   
79    ancient_author  ortho_word_las   
80    ancient_author  ortho_word_las   
81    ancient_author  ortho_word_las   
82    ancient_author  ortho_word_las   
83    ancient_author  ortho_word_las   
84    ancient_author  ortho_word_las   
85    ancient_author  ortho_word_las   
86    ancient_author  ortho_word_las   
87    ancient_author  ortho_word_las   
88    ancient_author  ortho_word_las   
89    ancient_author  ortho_word_las   
90    ancient_author  ortho_word_las   
91    ancient_author  ortho_word_las   
92    ancient_author  ortho_word_las   
93    ancient_author  ortho_word_las   
94    ancient_author  ortho_word_las   
95    ancient_author  ortho_word_las   
96    ancient_author  ortho_word_las   
97    ancient_author  ortho_word_las   
98    ancient_author  ortho_word_las   
99    anci

text_id
P313453    1
P313480    2
P313814    1
P314321    1
P334113    3
P334158    1
P334179    6
P334201    1
P334360    1
P334588    1
P334610    1
P334729    4
P334831    1
X900004    2
X900012    1
Name: cf, dtype: int64